#**Franchise Decision to Invest in Prominent Locations**

<a  align=center><img src = "https://www.qsrmagazine.com/sites/default/files/news-image/freddy-s-opens-first-international-location.jpg" width = 1200> </a>

<h1 align=center><font size = 5>Scrap Neighbourhoods Data - Geocoding Web Services - Foursquare Location Services</font></h1>

# **1. Import Libraries**

In [ ]:
!pip install folium==0.5.0

     |████████████████████████████████| 81kB 2.6MB/s 
  Created wheel for folium: filename=folium-0.5.0-cp36-none-any.whl size=76240 sha256=65f96259ba2dadaf3d1cb8579fc5ef86a218aff8d6497e07fdb078d2c139ca68
  Stored in directory: /root/.cache/pip/wheels/f8/98/ff/954791afc47740d554f0d9e5885fa09dd60c2265d42578e665
Successfully built folium
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.5.0 which is incompatible.
  Found existing installation: folium 0.8.3
    Uninstalling folium-0.8.3:
      Successfully uninstalled folium-0.8.3


In [ ]:
import pandas as pd
import numpy as np
import time
import requests, json
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim  #geopy is a Python client for several popular geocoding web services
from geopy.exc import GeocoderTimedOut
import folium
from sklearn.cluster import KMeans
print("Folium version = ", folium.__version__)

Folium version =  0.8.3


# **2. Get 4 cities data from Wikipedia**

## City1: Bengaluru Data

https://en.wikipedia.org/wiki/List_of_wards_in_Bangalore

In [ ]:
web_page = requests.get("https://en.wikipedia.org/wiki/List_of_wards_in_Bangalore").text
web_page

'<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>List of wards in Bangalore - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"17158df7-4a78-4fb4-9a59-1b714759cf3a","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_wards_in_Bangalore","wgTitle":"List of wards in Bangalore","wgCurRevisionId":982915192,"wgRevisionId":982915192,"wgArticleId":52468336,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Use dmy dates from January 2019","Use Indian English from January 2019","All Wikipedia articles written in Indian English",

In [ ]:
soup = BeautifulSoup(web_page)
soup

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of wards in Bangalore - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"17158df7-4a78-4fb4-9a59-1b714759cf3a","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_wards_in_Bangalore","wgTitle":"List of wards in Bangalore","wgCurRevisionId":982915192,"wgRevisionId":982915192,"wgArticleId":52468336,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Use dmy dates from January 2019","Use Indian English from January 2019","All Wikipedia articles written in Indian English","Banga

In [ ]:
table_tags = soup.find("table", class_='wikitable')
table_tags

<table class="wikitable">
<tbody><tr>
<th>Ward number
</th>
<th>Ward name
</th>
<th>Reservation category
</th>
<th>Assembly constituency<sup class="reference" id="cite_ref-2"><a href="#cite_note-2">[2]</a></sup>
</th>
<th>Lok Sabha constituency<sup class="reference" id="cite_ref-3"><a href="#cite_note-3">[3]</a></sup>
</th></tr>
<tr>
<td>1
</td>
<td>Kempegowda
</td>
<td>Backward Category B
</td>
<td><a class="mw-redirect" href="/wiki/Yelahanka_(Vidhan_Sabha_constituency)" title="Yelahanka (Vidhan Sabha constituency)">Yelahanka</a>
</td>
<td><a href="/wiki/Chikballapur_(Lok_Sabha_constituency)" title="Chikballapur (Lok Sabha constituency)">Chikballapur</a>
</td></tr>
<tr>
<td>2
</td>
<td>Chowdeshwari
</td>
<td>Backward Category A (Women)
</td>
<td><a class="mw-redirect" href="/wiki/Yelahanka_(Vidhan_Sabha_constituency)" title="Yelahanka (Vidhan Sabha constituency)">Yelahanka</a>
</td>
<td><a href="/wiki/Chikballapur_(Lok_Sabha_constituency)" title="Chikballapur (Lok Sabha constituency)"

In [ ]:
tr_tags = table_tags.find_all("tr")
tr_tags

[<tr>
 <th>Ward number
 </th>
 <th>Ward name
 </th>
 <th>Reservation category
 </th>
 <th>Assembly constituency<sup class="reference" id="cite_ref-2"><a href="#cite_note-2">[2]</a></sup>
 </th>
 <th>Lok Sabha constituency<sup class="reference" id="cite_ref-3"><a href="#cite_note-3">[3]</a></sup>
 </th></tr>, <tr>
 <td>1
 </td>
 <td>Kempegowda
 </td>
 <td>Backward Category B
 </td>
 <td><a class="mw-redirect" href="/wiki/Yelahanka_(Vidhan_Sabha_constituency)" title="Yelahanka (Vidhan Sabha constituency)">Yelahanka</a>
 </td>
 <td><a href="/wiki/Chikballapur_(Lok_Sabha_constituency)" title="Chikballapur (Lok Sabha constituency)">Chikballapur</a>
 </td></tr>, <tr>
 <td>2
 </td>
 <td>Chowdeshwari
 </td>
 <td>Backward Category A (Women)
 </td>
 <td><a class="mw-redirect" href="/wiki/Yelahanka_(Vidhan_Sabha_constituency)" title="Yelahanka (Vidhan Sabha constituency)">Yelahanka</a>
 </td>
 <td><a href="/wiki/Chikballapur_(Lok_Sabha_constituency)" title="Chikballapur (Lok Sabha constituency)">

In [ ]:
tr_tags[0]

<tr>
<th>Ward number
</th>
<th>Ward name
</th>
<th>Reservation category
</th>
<th>Assembly constituency<sup class="reference" id="cite_ref-2"><a href="#cite_note-2">[2]</a></sup>
</th>
<th>Lok Sabha constituency<sup class="reference" id="cite_ref-3"><a href="#cite_note-3">[3]</a></sup>
</th></tr>

In [ ]:
tr_tags.pop(0)

<tr>
<th>Ward number
</th>
<th>Ward name
</th>
<th>Reservation category
</th>
<th>Assembly constituency<sup class="reference" id="cite_ref-2"><a href="#cite_note-2">[2]</a></sup>
</th>
<th>Lok Sabha constituency<sup class="reference" id="cite_ref-3"><a href="#cite_note-3">[3]</a></sup>
</th></tr>

In [ ]:
tr_tags[0]

<tr>
<td>1
</td>
<td>Kempegowda
</td>
<td>Backward Category B
</td>
<td><a class="mw-redirect" href="/wiki/Yelahanka_(Vidhan_Sabha_constituency)" title="Yelahanka (Vidhan Sabha constituency)">Yelahanka</a>
</td>
<td><a href="/wiki/Chikballapur_(Lok_Sabha_constituency)" title="Chikballapur (Lok Sabha constituency)">Chikballapur</a>
</td></tr>

In [ ]:
blr_neighbourhoods=[]
for tr_tag in tr_tags:
    td_tags=tr_tag.find_all("td")
    blr_neighbourhoods.append(td_tags[1].text.split('\n')[0])

blr_neighbourhoods

['Kempegowda',
 'Chowdeshwari',
 'Attur',
 'Yelahanka Satellite Town',
 'Jakkur',
 'Thanisandra',
 'Byatarayanapura',
 'Kodigehalli',
 'Vidyaranyapura',
 'Doddabommasandra',
 'Kuvempu Nagar',
 'Shettyhalli',
 'Mallasandra',
 'Bagalagunte',
 'T-Dasarahalli',
 'Jalahalli',
 'J.P.Park',
 'Radhakrishna Temple',
 'Sanjay Nagar',
 'Ganga Nagar',
 'Hebbal',
 'Vishwanathnagenahalli',
 'Nagavara',
 'HBR Layout',
 'Horamavu',
 'Ramamurthy Nagar',
 'Banaswadi',
 'Kammanahalli',
 'Kacharakanahalli',
 'Kadugondanahalli',
 'Kushal Nagar',
 'Kavalbyrasandra',
 'Manorayanapalya',
 'Gangenahalli',
 'Aramane Nagar',
 'Mathikere',
 'Yeshwanthpur',
 'H.M.T',
 'Chokkasandra',
 'Dodda Bidarkallu',
 'Peenya Industrial Area',
 'Lakshmidevi Nagar',
 'Nandini Layout',
 'Marappana Palya',
 'Malleshwaram',
 'Jayachamarajendra Nagar',
 'Devarajeevanahalli',
 'Muneshwara Nagar',
 'Lingarajapuram',
 'Benniganahalli',
 'Vijinapura',
 'K.R.Puram',
 'Basavanapura',
 'Hoodi',
 'Devasandra',
 'A.Narayanapura',
 'C.V.Rama

In [ ]:
print("Number of Bangalore Neighbourhoods: ", len(blr_neighbourhoods))

Number of Bangalore Neighbourhoods:  198


In [ ]:
df_blr = pd.DataFrame(blr_neighbourhoods, columns=['Neighbourhood'])
df_blr['City']='Bengaluru'
df_blr['State']='KA'
df_blr['Country']='India'

df_blr.head()

Neighbourhood       City State Country
0                Kempegowda  Bengaluru    KA   India
1              Chowdeshwari  Bengaluru    KA   India
2                     Attur  Bengaluru    KA   India
3  Yelahanka Satellite Town  Bengaluru    KA   India
4                    Jakkur  Bengaluru    KA   India

## City2: Seoul Data

https://en.wikipedia.org/wiki/List_of_districts_of_Seoul

In [ ]:
web_page = requests.get("https://en.wikipedia.org/wiki/List_of_districts_of_Seoul").text
web_page

'<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>List of districts of Seoul - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"148a4d57-0c9d-4a5d-bf01-39b6bf75fd6d","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_districts_of_Seoul","wgTitle":"List of districts of Seoul","wgCurRevisionId":975452685,"wgRevisionId":975452685,"wgArticleId":8684865,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles containing Korean-language text","Geography of Seoul","Government of Seoul","Districts of Seoul","Seoul-related lis

In [ ]:
soup = BeautifulSoup(web_page)
soup

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of districts of Seoul - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"148a4d57-0c9d-4a5d-bf01-39b6bf75fd6d","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_districts_of_Seoul","wgTitle":"List of districts of Seoul","wgCurRevisionId":975452685,"wgRevisionId":975452685,"wgArticleId":8684865,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles containing Korean-language text","Geography of Seoul","Government of Seoul","Districts of Seoul","Seoul-related lists"],"

In [ ]:
table_tag = soup.find("table", class_='wikitable')
table_tag

<table class="wikitable sortable">
<tbody><tr>
<th>Name</th>
<th>Population</th>
<th>Area</th>
<th>Population density
</th></tr>
<tr>
<td><a class="mw-redirect" href="/wiki/Dobong-gu" title="Dobong-gu">Dobong-gu</a> (도봉구; <span lang="ko" title="Korean language text"><a class="extiw" href="https://en.wiktionary.org/wiki/%E9%81%93" title="wikt:道">道</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%B3%B0" title="wikt:峰">峰</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%8D%80" title="wikt:區">區</a></span>)
</td>
<td>355,712
</td>
<td>20.70 km²
</td>
<td>17184/km²
</td></tr>
<tr>
<td><a class="mw-redirect" href="/wiki/Dongdaemun-gu" title="Dongdaemun-gu">Dongdaemun-gu</a> (동대문구; <span lang="ko" title="Korean language text"><a class="extiw" href="https://en.wiktionary.org/wiki/%E6%9D%B1" title="wikt:東">東</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%A4%A7" title="wikt:大">大</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E9%96%80" title="wikt:門"

In [ ]:
tr_tags = table_tag.find_all("tr")
tr_tags

[<tr>
 <th>Name</th>
 <th>Population</th>
 <th>Area</th>
 <th>Population density
 </th></tr>, <tr>
 <td><a class="mw-redirect" href="/wiki/Dobong-gu" title="Dobong-gu">Dobong-gu</a> (도봉구; <span lang="ko" title="Korean language text"><a class="extiw" href="https://en.wiktionary.org/wiki/%E9%81%93" title="wikt:道">道</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%B3%B0" title="wikt:峰">峰</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%8D%80" title="wikt:區">區</a></span>)
 </td>
 <td>355,712
 </td>
 <td>20.70 km²
 </td>
 <td>17184/km²
 </td></tr>, <tr>
 <td><a class="mw-redirect" href="/wiki/Dongdaemun-gu" title="Dongdaemun-gu">Dongdaemun-gu</a> (동대문구; <span lang="ko" title="Korean language text"><a class="extiw" href="https://en.wiktionary.org/wiki/%E6%9D%B1" title="wikt:東">東</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%A4%A7" title="wikt:大">大</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E9%96%80" title="wikt:門">門</a><a class="extiw" hr

In [ ]:
tr_tags[0]

<tr>
<th>Name</th>
<th>Population</th>
<th>Area</th>
<th>Population density
</th></tr>

In [ ]:
tr_tags.pop(0)

<tr>
<th>Name</th>
<th>Population</th>
<th>Area</th>
<th>Population density
</th></tr>

In [ ]:
tr_tags[0]

<tr>
<td><a class="mw-redirect" href="/wiki/Dobong-gu" title="Dobong-gu">Dobong-gu</a> (도봉구; <span lang="ko" title="Korean language text"><a class="extiw" href="https://en.wiktionary.org/wiki/%E9%81%93" title="wikt:道">道</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%B3%B0" title="wikt:峰">峰</a><a class="extiw" href="https://en.wiktionary.org/wiki/%E5%8D%80" title="wikt:區">區</a></span>)
</td>
<td>355,712
</td>
<td>20.70 km²
</td>
<td>17184/km²
</td></tr>

In [ ]:
sul_neighbourhoods=[]
for tr_tag in tr_tags[0:-1]:
    td_tags=tr_tag.find_all("td")
    sul_neighbourhoods.append(td_tags[0].text.split(' ')[0])

sul_neighbourhoods

['Dobong-gu',
 'Dongdaemun-gu',
 'Dongjak-gu',
 'Eunpyeong-gu',
 'Gangbuk-gu',
 'Gangdong-gu',
 'Gangnam-gu',
 'Gangseo-gu',
 'Geumcheon-gu',
 'Guro-gu',
 'Gwanak-gu',
 'Gwangjin-gu',
 'Jongno-gu',
 'Jung-gu',
 'Jungnang-gu',
 'Mapo-gu',
 'Nowon-gu',
 'Seocho-gu',
 'Seodaemun-gu',
 'Seongbuk-gu',
 'Seongdong-gu',
 'Songpa-gu',
 'Yangcheon-gu',
 'Yeongdeungpo-gu',
 'Yongsan-gu']

In [ ]:
df_sul = pd.DataFrame(sul_neighbourhoods, columns=['Neighbourhood'])
df_sul['City']='Seoul'
df_sul['State']='Gyeonggi'
df_sul['Country']='South Korea'

df_sul.head()

Neighbourhood   City     State      Country
0      Dobong-gu  Seoul  Gyeonggi  South Korea
1  Dongdaemun-gu  Seoul  Gyeonggi  South Korea
2     Dongjak-gu  Seoul  Gyeonggi  South Korea
3   Eunpyeong-gu  Seoul  Gyeonggi  South Korea
4     Gangbuk-gu  Seoul  Gyeonggi  South Korea

## City3: Vancouver Data

https://en.wikipedia.org/wiki/List_of_neighbourhoods_in_Vancouver

In [ ]:
web_page = requests.get("https://en.wikipedia.org/wiki/List_of_neighbourhoods_in_Vancouver").text
web_page

'<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>List of neighbourhoods in Vancouver - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"bcde54e0-a6ad-48ec-ba80-9b930a4585bf","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighbourhoods_in_Vancouver","wgTitle":"List of neighbourhoods in Vancouver","wgCurRevisionId":980625626,"wgRevisionId":980625626,"wgArticleId":17757023,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles needing additional references from January 2009","All articles needing additional refer

In [ ]:
soup = BeautifulSoup(web_page)
soup

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of neighbourhoods in Vancouver - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"bcde54e0-a6ad-48ec-ba80-9b930a4585bf","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighbourhoods_in_Vancouver","wgTitle":"List of neighbourhoods in Vancouver","wgCurRevisionId":980625626,"wgRevisionId":980625626,"wgArticleId":17757023,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles needing additional references from January 2009","All articles needing additional references"

In [ ]:
div_tag = soup.find(class_= 'mw-parser-output')
div_tag

<div class="mw-parser-output"><table class="box-More_citations_needed plainlinks metadata ambox ambox-content ambox-Refimprove" role="presentation"><tbody><tr><td class="mbox-image"><div style="width:52px"><a class="image" href="/wiki/File:Question_book-new.svg"><img alt="" data-file-height="399" data-file-width="512" decoding="async" height="39" src="//upload.wikimedia.org/wikipedia/en/thumb/9/99/Question_book-new.svg/50px-Question_book-new.svg.png" srcset="//upload.wikimedia.org/wikipedia/en/thumb/9/99/Question_book-new.svg/75px-Question_book-new.svg.png 1.5x, //upload.wikimedia.org/wikipedia/en/thumb/9/99/Question_book-new.svg/100px-Question_book-new.svg.png 2x" width="50"/></a></div></td><td class="mbox-text"><div class="mbox-text-span">This article <b>needs additional citations for <a href="/wiki/Wikipedia:Verifiability" title="Wikipedia:Verifiability">verification</a></b>.<span class="hide-when-compact"> Please help <a class="external text" href="https://en.wikipedia.org/w/index.

In [ ]:
li_tags = div_tag.find_all('li')
li_tags

[<li class="toclevel-1 tocsection-1"><a href="#Official_neighbourhoods"><span class="tocnumber">1</span> <span class="toctext">Official neighbourhoods</span></a></li>,
 <li class="toclevel-1 tocsection-2"><a href="#Other_areas"><span class="tocnumber">2</span> <span class="toctext">Other areas</span></a></li>,
 <li class="toclevel-1 tocsection-3"><a href="#See_also"><span class="tocnumber">3</span> <span class="toctext">See also</span></a></li>,
 <li class="toclevel-1 tocsection-4"><a href="#References"><span class="tocnumber">4</span> <span class="toctext">References</span></a></li>,
 <li class="toclevel-1 tocsection-5"><a href="#External_links"><span class="tocnumber">5</span> <span class="toctext">External links</span></a></li>,
 <li><a href="/wiki/Arbutus_Ridge" title="Arbutus Ridge">Arbutus Ridge</a> - Located in the middle of Vancouver's west side, characterized by tree-lined streets and heritage homes with large lot sizes.</li>,
 <li><a href="/wiki/Downtown_Vancouver" title="Dow

In [ ]:
li_tags[5:30]

[<li><a href="/wiki/Fairview,_Vancouver" title="Fairview, Vancouver">Fairview</a> - Contains the popular attractions of <a href="/wiki/Granville_Island" title="Granville Island">Granville Island</a> and the <a href="/wiki/South_Granville_Rise" title="South Granville Rise">South Granville</a> shopping district. The neighbourhood is also the location of the <a href="/wiki/Vancouver_General_Hospital" title="Vancouver General Hospital">Vancouver General Hospital</a> and contains many health-related institutions.</li>,
 <li><a href="/wiki/Grandview%E2%80%93Woodland" title="Grandview–Woodland">Grandview-Woodland</a> - A mature neighbourhood in east Vancouver that is a diverse mixture of commercial, industrial, single-family and multi-family residential dwellings with a rich ethnic history and features.</li>,
 <li><a href="/wiki/Hastings%E2%80%93Sunrise" title="Hastings–Sunrise">Hastings-Sunrise</a> - One of Vancouver's oldest neighbourhoods, it is mainly residential, with a dense strip of sh

In [ ]:
li_tags[8].text

'Fairview - Contains the popular attractions of Granville Island and the South Granville shopping district. The neighbourhood is also the location of the Vancouver General Hospital and contains many health-related institutions.'

In [ ]:
vnc_neighbourhoods=[]
for li_tag in li_tags[8:30]:
    td_tags=li_tag.find_all("li")
    vnc_neighbourhoods.append(li_tag.text.split(' ')[0])

vnc_neighbourhoods

['Fairview - Contains the popular attractions of Granville Island and the South Granville shopping district. The neighbourhood is also the location of the Vancouver General Hospital and contains many health-related institutions.',
 'Grandview-Woodland - A mature neighbourhood in east Vancouver that is a diverse mixture of commercial, industrial, single-family and multi-family residential dwellings with a rich ethnic history and features.',
 "Hastings-Sunrise - One of Vancouver's oldest neighbourhoods, it is mainly residential, with a dense strip of shops along Hastings Street. It is also known for being the home of Hastings Park and the Pacific National Exhibition.",
 'Kensington-Cedar Cottage - One of the most multicultural neighbourhoods in the city and located in the middle of east Vancouver. It is the location of Trout Lake.',
 'Kerrisdale - A primarily residential neighbourhood bisected by the Arbutus Greenway and containing the Kerrisdale Village shopping area.',
 'Killarney - Lo

In [ ]:
df_vnc = pd.DataFrame(vnc_neighbourhoods, columns=['Neighbourhood'])
df_vnc['City']='Vancouver'
df_vnc['State']='BC'
df_vnc['Country']='Canada'

df_vnc.head()

Neighbourhood       City State Country
0  Fairview - Contains the popular attractions of...  Vancouver    BC  Canada
1  Grandview-Woodland - A mature neighbourhood in...  Vancouver    BC  Canada
2  Hastings-Sunrise - One of Vancouver's oldest n...  Vancouver    BC  Canada
3  Kensington-Cedar Cottage - One of the most mul...  Vancouver    BC  Canada
4  Kerrisdale - A primarily residential neighbour...  Vancouver    BC  Canada

## City4: San Francisco Data

https://en.wikipedia.org/wiki/List_of_neighborhoods_in_San_Francisco

In [ ]:
web_page = requests.get("https://en.wikipedia.org/wiki/List_of_neighborhoods_in_San_Francisco").text
web_page

'<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>List of neighborhoods in San Francisco - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"436031e6-954c-4780-9263-f8b3788bc55b","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighborhoods_in_San_Francisco","wgTitle":"List of neighborhoods in San Francisco","wgCurRevisionId":981828548,"wgRevisionId":981828548,"wgArticleId":1487556,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["CS1 maint: archived copy as title","Webarchive template archiveis links","Webarchive tem

In [ ]:
soup = BeautifulSoup(web_page)
soup

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of neighborhoods in San Francisco - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"436031e6-954c-4780-9263-f8b3788bc55b","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighborhoods_in_San_Francisco","wgTitle":"List of neighborhoods in San Francisco","wgCurRevisionId":981828548,"wgRevisionId":981828548,"wgArticleId":1487556,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["CS1 maint: archived copy as title","Webarchive template archiveis links","Webarchive template 

In [ ]:
toc_tags = soup.find_all(class_='toctext')
toc_tags

[<span class="toctext">Alamo Square</span>,
 <span class="toctext">Anza Vista</span>,
 <span class="toctext">Ashbury Heights</span>,
 <span class="toctext">Balboa Park</span>,
 <span class="toctext">Balboa Terrace</span>,
 <span class="toctext">Bayview</span>,
 <span class="toctext">Belden Place</span>,
 <span class="toctext">Bernal Heights</span>,
 <span class="toctext">Buena Vista</span>,
 <span class="toctext">Butchertown (Old and New)</span>,
 <span class="toctext">Castro</span>,
 <span class="toctext">Cathedral Hill</span>,
 <span class="toctext">Cayuga Terrace</span>,
 <span class="toctext">China Basin</span>,
 <span class="toctext">Chinatown</span>,
 <span class="toctext">Civic Center</span>,
 <span class="toctext">Clarendon Heights</span>,
 <span class="toctext">Cole Valley</span>,
 <span class="toctext">Corona Heights</span>,
 <span class="toctext">Cow Hollow</span>,
 <span class="toctext">Crocker-Amazon</span>,
 <span class="toctext">Design District</span>,
 <span class="toct

In [ ]:
sfr_neighbourhoods=[]
for toc_tag in toc_tags[:-4]:
  sfr_neighbourhoods.append(toc_tag.text)

sfr_neighbourhoods

['Alamo Square',
 'Anza Vista',
 'Ashbury Heights',
 'Balboa Park',
 'Balboa Terrace',
 'Bayview',
 'Belden Place',
 'Bernal Heights',
 'Buena Vista',
 'Butchertown (Old and New)',
 'Castro',
 'Cathedral Hill',
 'Cayuga Terrace',
 'China Basin',
 'Chinatown',
 'Civic Center',
 'Clarendon Heights',
 'Cole Valley',
 'Corona Heights',
 'Cow Hollow',
 'Crocker-Amazon',
 'Design District',
 'Diamond Heights',
 'Dogpatch',
 'Dolores Heights',
 'Duboce Triangle',
 'Embarcadero',
 'Eureka Valley',
 'Excelsior',
 'Fillmore',
 'Financial District',
 'Financial District South',
 "Fisherman's Wharf",
 'Forest Hill',
 'Forest Knolls',
 'Glen Park',
 'Golden Gate Heights',
 'Haight-Ashbury',
 'Hayes Valley',
 'Hunters Point',
 'India Basin',
 'Ingleside',
 'Ingleside Terraces',
 'Inner Sunset',
 'Irish Hill',
 'Islais Creek',
 'Jackson Square',
 'Japantown',
 'Jordan Park',
 'Laguna Honda',
 'Lake Street',
 'Lakeside',
 'Lakeshore',
 'Laurel Heights',
 'Lincoln Manor',
 'Little Hollywood',
 'Little 

In [ ]:
df_sfr = pd.DataFrame(sfr_neighbourhoods, columns=['Neighbourhood'])
df_sfr['City']='San Francisco'
df_sfr['State']='CA'
df_sfr['Country']='USA'

df_sfr.head()

Neighbourhood           City State Country
0     Alamo Square  San Francisco    CA     USA
1       Anza Vista  San Francisco    CA     USA
2  Ashbury Heights  San Francisco    CA     USA
3      Balboa Park  San Francisco    CA     USA
4   Balboa Terrace  San Francisco    CA     USA

## Merge 4 cities in one DataFrame

In [ ]:
df = pd.concat([df_blr, df_sul, df_vnc, df_sfr], ignore_index=True)
df

Neighbourhood           City State Country
0                  Kempegowda      Bengaluru    KA   India
1                Chowdeshwari      Bengaluru    KA   India
2                       Attur      Bengaluru    KA   India
3    Yelahanka Satellite Town      Bengaluru    KA   India
4                      Jakkur      Bengaluru    KA   India
..                        ...            ...   ...     ...
359               West Portal  San Francisco    CA     USA
360          Western Addition  San Francisco    CA     USA
361        Westwood Highlands  San Francisco    CA     USA
362             Westwood Park  San Francisco    CA     USA
363               Yerba Buena  San Francisco    CA     USA

[364 rows x 4 columns]

In [ ]:
#save consolidated df into an excel file
df.to_excel("Neighbourhoods.xlsx", index=False)

# **3. Getting Geocodes**

## Check Neighbourhoods Coordinates

In [ ]:
#test Geocode
geolocator = Nominatim(user_agent='Markov_Applied_DS')
location = geolocator.geocode("dokki, egypt")
location

Location(الدقى, شارع التحرير, شارع الدقى, بولاق الدكرور, محافظة الجيزة‎, 11231, Egypt / مصر, (30.0382381, 31.2120051, 0.0))

In [ ]:
#read consolidated df from the excel file
df = pd.read_excel("Neighbourhoods.xlsx")

In [ ]:
df.head()

Neighbourhood       City State Country
0                Kempegowda  Bengaluru    KA   India
1              Chowdeshwari  Bengaluru    KA   India
2                     Attur  Bengaluru    KA   India
3  Yelahanka Satellite Town  Bengaluru    KA   India
4                    Jakkur  Bengaluru    KA   India

In [ ]:
df.shape

(364, 4)

In [ ]:
#test df.iterrows
for index, data in df.iterrows():
    print(index)
    print("---")
    print(data)
    print("---")
    print(data['Neighbourhood'] + ', ' + data['City'] + ', ' + data['State'])
    break

0
---
Neighbourhood    Kempegowda
City              Bengaluru
State                    KA
Country               India
Name: 0, dtype: object
---
Kempegowda, Bengaluru, KA


In [ ]:
latitude=[]
longitude=[]

for index, data in df.iterrows():
    address = data['Neighbourhood'] + ', ' + data['City'] + ', ' + data['State']
    
    try:
        geolocator = Nominatim(user_agent='Markov_Applied_DS')
        location = geolocator.geocode(address)
    except GeocoderTimedOut as err:
        print(err)
        latitude.append('timeout')
        longitude.append('timeout')
    else:
        if location is not None:
            latitude.append(location.latitude)
            longitude.append(location.longitude)
            print('The geograpical coordinate of {} are {}, {}.'.format(address, location.latitude, location.longitude))
        else:
            latitude.append(None)
            longitude.append(None)
            print('None Coordinates for {}'.format(address))
        time.sleep(2.0)

print("=================================")
print("=================================")
print("Total Latitude: ", len(latitude))
print("Total Longitude: ", len(longitude))

The geograpical coordinate of Kempegowda, Bengaluru, KA are 13.10901775, 77.60190027360827.
The geograpical coordinate of Chowdeshwari, Bengaluru, KA are 12.92519, 77.5880201.
The geograpical coordinate of Attur, Bengaluru, KA are 13.11148165, 77.56305557563954.
The geograpical coordinate of Yelahanka Satellite Town, Bengaluru, KA are 13.089139249999999, 77.5827165877116.
The geograpical coordinate of Jakkur, Bengaluru, KA are 13.0784743, 77.6068938.
The geograpical coordinate of Thanisandra, Bengaluru, KA are 13.054713, 77.6339258.
The geograpical coordinate of Byatarayanapura, Bengaluru, KA are 13.062073550000001, 77.59639164365345.
The geograpical coordinate of Kodigehalli, Bengaluru, KA are 13.0601125, 77.5767725.
The geograpical coordinate of Vidyaranyapura, Bengaluru, KA are 13.0766407, 77.5577315.
The geograpical coordinate of Doddabommasandra, Bengaluru, KA are 13.0649673, 77.56296570598985.
The geograpical coordinate of Kuvempu Nagar, Bengaluru, KA are 13.07319265, 77.54171340

In [ ]:
df['Latitude'] = latitude
df['Longitude'] = longitude

df

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...        NaN         NaN
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

In [ ]:
print("Neighbourhoods with None Coordinates: ", sum(df['Latitude'].isna()))
print("Neighbourhoods with Timeout Error: ", sum(df['Latitude']=='timeout'))

Neighbourhoods with None Coordinates:  70
Neighbourhoods with Timeout Error:  0


/usr/local/lib/python3.6/dist-packages/pandas/core/ops/array_ops.py:253: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  res_values = method(rvalues)


In [ ]:
df.to_excel("Neighbourhoods_Geolocations.xlsx", index=False)

In [ ]:
(df[df['Latitude'].isna()]['City']).value_counts()

Bengaluru        32
San Francisco    23
Seoul            15
Name: City, dtype: int64

## Check Neighbourhoods with None Coordinates

In [ ]:
df = pd.read_excel("Neighbourhoods_Geolocations.xlsx")

In [ ]:
df[df['Latitude'].isnull()]

Neighbourhood           City State Country  Latitude  Longitude
21   Vishwanathnagenahalli      Bengaluru    KA   India       NaN        NaN
39        Dodda Bidarkallu      Bengaluru    KA   India       NaN        NaN
43         Marappana Palya      Bengaluru    KA   India       NaN        NaN
46      Devarajeevanahalli      Bengaluru    KA   India       NaN        NaN
50              Vijanapura      Bengaluru    KA   India       NaN        NaN
..                     ...            ...   ...     ...       ...        ...
317       Monterey Heights  San Francisco    CA     USA       NaN        NaN
330             Polk Gulch  San Francisco    CA     USA       NaN        NaN
355       University Mound  San Francisco    CA     USA       NaN        NaN
356           Upper Market  San Francisco    CA     USA       NaN        NaN
361     Westwood Highlands  San Francisco    CA     USA       NaN        NaN

[70 rows x 6 columns]

In [ ]:
latitude_nan=[]
longitude_nan=[]

for index, data in df[df['Latitude'].isnull()].iterrows():
    address = data['Neighbourhood'] + ', ' + data['City']
    
    try:
        geolocator = Nominatim(user_agent='Markov_Applied_DS')
        location = geolocator.geocode(address)
    except GeocoderTimedOut as err:
        print(err)
        latitude_nan.append('timeout')
        longitude_nan.append('timeout')
    else:
        if location is not None:
            latitude_nan.append(location.latitude)
            longitude_nan.append(location.longitude)
            print('The geograpical coordinate of {} are {}, {}.'.format(address, location.latitude, location.longitude))
        else:
            latitude_nan.append(None)
            longitude_nan.append(None)
            print('None Coordinates for {}'.format(address))
        time.sleep(2.0)

print("=================================")
print("=================================")
print("Total Latitude: ", len(latitude_nan))
print("Total Longitude: ", len(longitude_nan))

None Coordinates for Vishwanathnagenahalli, Bengaluru
None Coordinates for Dodda Bidarkallu, Bengaluru
None Coordinates for Marappana Palya, Bengaluru
None Coordinates for Devarajeevanahalli, Bengaluru
The geograpical coordinate of Vijanapura, Bengaluru are 13.0032009, 77.6678609.
None Coordinates for Hosathippasandra, Bengaluru
None Coordinates for Maruthiseva Nagar, Bengaluru
None Coordinates for Sagayapuram, Bengaluru
None Coordinates for Kadumalleshwara, Bengaluru
None Coordinates for Shakthiganapathi Nagar, Bengaluru
None Coordinates for Shankaramata, Bengaluru
None Coordinates for Dattathreya Temple, Bengaluru
None Coordinates for Pulikeshi Nagar, Bengaluru
The geograpical coordinate of Vignana Nagar, Bengaluru are 15.8031414, 78.0415184.
None Coordinates for Kadugudi, Bengaluru
None Coordinates for Hagadooru, Bengaluru
None Coordinates for Vrushabhavathi, Bengaluru
None Coordinates for Govindraja Nagara, Bengaluru
None Coordinates for Sri Rammandira, Bengaluru
None Coordinates f

In [ ]:
#test check null
df.isnull().any(axis=1)

0      False
1      False
2      False
3      False
4      False
       ...  
359    False
360    False
361    False
362    False
363    False
Length: 364, dtype: bool

In [ ]:
df_nan = pd.DataFrame(index=df.index[df.isnull().any(axis=1)], data=list(zip(latitude_nan, longitude_nan)), columns=['Latitude', 'Longitude'])

In [ ]:
df_nan

Latitude   Longitude
21         NaN         NaN
39         NaN         NaN
43         NaN         NaN
46         NaN         NaN
50   13.003201   77.667861
..         ...         ...
317  32.512085  -85.090769
330  41.649466  -93.500067
355  55.949511   -3.195349
356  16.417114  120.592371
361  14.286750  120.944712

[70 rows x 2 columns]

In [ ]:
df = df.fillna(df_nan)
df

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...  14.286750  120.944712
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

In [ ]:
df[df['Latitude'].isnull()]

Neighbourhood           City  ... Latitude Longitude
21             Vishwanathnagenahalli      Bengaluru  ...      NaN       NaN
39                  Dodda Bidarkallu      Bengaluru  ...      NaN       NaN
43                   Marappana Palya      Bengaluru  ...      NaN       NaN
46                Devarajeevanahalli      Bengaluru  ...      NaN       NaN
57                  Hosathippasandra      Bengaluru  ...      NaN       NaN
58                 Maruthiseva Nagar      Bengaluru  ...      NaN       NaN
59                       Sagayapuram      Bengaluru  ...      NaN       NaN
64                   Kadumalleshwara      Bengaluru  ...      NaN       NaN
73            Shakthiganapathi Nagar      Bengaluru  ...      NaN       NaN
74                      Shankaramata      Bengaluru  ...      NaN       NaN
76                Dattathreya Temple      Bengaluru  ...      NaN       NaN
77                   Pulikeshi Nagar      Bengaluru  ...      NaN       NaN
82                          Kadugudi      Bengaluru  ...      NaN       NaN
83                         Hagadooru      Bengaluru  ...      NaN       NaN
101                   Vrushabhavathi      Bengaluru  ...      NaN       NaN
103                Govindraja Nagara      Bengaluru  ...      NaN       NaN
107                   Sri Rammandira      Bengaluru  ...      NaN       NaN
110                  Shanthala Nagar      Bengaluru  ...      NaN       NaN
118      Dharmarayaswamy Temple Ward      Bengaluru  ...      NaN       NaN
120                         Binnipet      Bengaluru  ...      NaN       NaN
128               Jnanabharathi Ward      Bengaluru  ...      NaN       NaN
130                   Nayandanahalli      Bengaluru  ...      NaN       NaN
135              Jagareevanram Nagar      Bengaluru  ...      NaN       NaN
142                  Visvesvarapuram      Bengaluru  ...      NaN       NaN
151                  Sudduguntepalya      Bengaluru  ...      NaN       NaN
152                         Jayangar      Bengaluru  ...      NaN       NaN
156  Gali Anjaneya Swamy Temple Ward      Bengaluru  ...      NaN       NaN
164               Ganeshmandira Ward      Bengaluru  ...      NaN       NaN
195                        Anjanapur      Bengaluru  ...      NaN       NaN
254        Butchertown (Old and New)  San Francisco  ...      NaN       NaN
287               Ingleside Terraces  San Francisco  ...      NaN       NaN
306                   Lower Nob Hill  San Francisco  ...      NaN       NaN

[32 rows x 6 columns]

In [ ]:
print("Neighbourhoods with None Coordinates: ", sum(df['Latitude'].isna()))

Neighbourhoods with None Coordinates:  32


In [ ]:
df.to_excel("Neighbourhoods_Geolocations_v2.xlsx", index=False)

## Check Last Neighbourhoods with None Coordinates

In [ ]:
df = pd.read_excel("Neighbourhoods_Geolocations_v2.xlsx")

In [ ]:
df_neigh = df.copy().set_index('Neighbourhood')
df_neigh

City State Country   Latitude   Longitude
Neighbourhood                                                               
Kempegowda                    Bengaluru    KA   India  13.109018   77.601900
Chowdeshwari                  Bengaluru    KA   India  12.925190   77.588020
Attur                         Bengaluru    KA   India  13.111482   77.563056
Yelahanka Satellite Town      Bengaluru    KA   India  13.089139   77.582717
Jakkur                        Bengaluru    KA   India  13.078474   77.606894
...                                 ...   ...     ...        ...         ...
West Portal               San Francisco    CA     USA  37.741141 -122.465634
Western Addition          San Francisco    CA     USA  37.779559 -122.429810
Westwood Highlands        San Francisco    CA     USA  14.286750  120.944712
Westwood Park             San Francisco    CA     USA  49.277466 -122.777594
Yerba Buena               San Francisco    CA     USA  -6.991968  -78.373201

[364 rows x 5 columns]

In [ ]:
df_neigh.loc['Vishwanathnagenahalli', 'Latitude'] = 13.0388
df_neigh.loc['Vishwanathnagenahalli', 'Longitude'] = 77.6041

df_neigh.loc['Dodda Bidarkallu', 'Latitude'] = 13.0333
df_neigh.loc['Dodda Bidarkallu', 'Longitude'] = 77.4906

df_neigh.loc['Marappana Palya', 'Latitude'] = 13.0206
df_neigh.loc['Marappana Palya', 'Longitude'] = 77.5516

df_neigh.loc['Devarajeevanahalli', 'Latitude'] = 13.0109
df_neigh.loc['Devarajeevanahalli', 'Longitude'] = 77.6095

df_neigh.loc['Hosathippasandra', 'Latitude'] = 12.973936
df_neigh.loc['Hosathippasandra', 'Longitude'] = 77.6509982

df_neigh.loc['Maruthiseva Nagar', 'Latitude'] = 13.0014
df_neigh.loc['Maruthiseva Nagar', 'Longitude'] = 77.6298

df_neigh.loc['Sagayapuram', 'Latitude'] = 13.0066
df_neigh.loc['Sagayapuram', 'Longitude'] = 77.6203

df_neigh.loc['Kadumalleshwara', 'Latitude'] = 13.3826
df_neigh.loc['Kadumalleshwara', 'Longitude'] = 77.2611

df_neigh.loc['Shakthiganapathi Nagar', 'Latitude'] = 12.9923
df_neigh.loc['Shakthiganapathi Nagar', 'Longitude'] = 77.5372

df_neigh.loc['Shankaramata', 'Latitude'] = 17.4008
df_neigh.loc['Shankaramata', 'Longitude'] = 78.5080

df_neigh.loc['Dattathreya Temple', 'Latitude'] = 12.9343
df_neigh.loc['Dattathreya Temple', 'Longitude'] = 77.5659

df_neigh.loc['Pulikeshi Nagar', 'Latitude'] = 12.9970
df_neigh.loc['Pulikeshi Nagar', 'Longitude'] = 77.6144

df_neigh.loc['Kadugudi', 'Latitude'] = 12.9908
df_neigh.loc['Kadugudi', 'Longitude'] = 77.7608

df_neigh.loc['Hagadooru', 'Latitude'] = 12.9661
df_neigh.loc['Hagadooru', 'Longitude'] = 77.7570

df_neigh.loc['Vrushabhavathi', 'Latitude'] = 12.9427
df_neigh.loc['Vrushabhavathi', 'Longitude'] = 77.5680

df_neigh.loc['Govindraja Nagara', 'Latitude'] = 12.9763
df_neigh.loc['Govindraja Nagara', 'Longitude'] = 77.5354

df_neigh.loc['Sri Rammandira', 'Latitude'] = 12.9417
df_neigh.loc['Sri Rammandira', 'Longitude'] = 77.6192

df_neigh.loc['Shanthala Nagar', 'Latitude'] = 12.9717
df_neigh.loc['Shanthala Nagar', 'Longitude'] = 77.6006

df_neigh.loc['Dharmarayaswamy Temple Ward', 'Latitude'] = 12.9653
df_neigh.loc['Dharmarayaswamy Temple Ward', 'Longitude'] = 77.5832

df_neigh.loc['Binnipet', 'Latitude'] = 12.9654
df_neigh.loc['Binnipet', 'Longitude'] = 77.5617

df_neigh.loc['Jnanabharathi Ward', 'Latitude'] = 12.9779
df_neigh.loc['Jnanabharathi Ward', 'Longitude'] = 77.5027

df_neigh.loc['Nayandanahalli', 'Latitude'] = 12.9446
df_neigh.loc['Nayandanahalli', 'Longitude'] = 77.5256

df_neigh.loc['Jagareevanram Nagar', 'Latitude'] = 12.9656
df_neigh.loc['Jagareevanram Nagar', 'Longitude'] = 77.5507

df_neigh.loc['Visvesvarapuram', 'Latitude'] = 12.9501
df_neigh.loc['Visvesvarapuram', 'Longitude'] = 77.5784

df_neigh.loc['Sudduguntepalya', 'Latitude'] = 12.9828
df_neigh.loc['Sudduguntepalya', 'Longitude'] = 77.6550

df_neigh.loc['Jayangar', 'Latitude'] = 12.9308
df_neigh.loc['Jayangar', 'Longitude'] = 77.5838

df_neigh.loc['Gali Anjaneya Swamy Temple Ward', 'Latitude'] = 12.9367
df_neigh.loc['Gali Anjaneya Swamy Temple Ward', 'Longitude'] = 77.5497

df_neigh.loc['Ganeshmandira Ward', 'Latitude'] = 12.9279
df_neigh.loc['Ganeshmandira Ward', 'Longitude'] = 77.5692

df_neigh.loc['Anjanapur', 'Latitude'] = 12.8549
df_neigh.loc['Anjanapur', 'Longitude'] = 77.5543

df_neigh.loc['Butchertown (Old and New)', 'Latitude'] = 38.2569
df_neigh.loc['Butchertown (Old and New)', 'Longitude'] = -85.7287

df_neigh.loc['Ingleside Terraces', 'Latitude'] = 37.7198
df_neigh.loc['Ingleside Terraces', 'Longitude'] = -122.4538

df_neigh.loc['Lower Nob Hill', 'Latitude'] = 37.7890
df_neigh.loc['Lower Nob Hill', 'Longitude'] = -122.4109

In [ ]:
df_neigh.reset_index(inplace=True)
df_neigh

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...  14.286750  120.944712
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

In [ ]:
df_neigh[df_neigh['Latitude'].isna()]

Empty DataFrame
Columns: [Neighbourhood, City, State, Country, Latitude, Longitude]
Index: []

In [ ]:
df_neigh.to_excel("Neighbourhoods_Geolocations_v3.xlsx", index=False)

# **4. Drawing Neighbourhoods/Cities Maps**

## Cities Map

In [ ]:
df_map = pd.read_excel("Neighbourhoods_Geolocations_v3.xlsx")

In [ ]:
df_map

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...  14.286750  120.944712
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

In [ ]:
df_map.groupby('City').count()

Neighbourhood  State  Country  Latitude  Longitude
City                                                             
Bengaluru                198    198      198       198        198
San Francisco            119    119      119       119        119
Seoul                     25     25       25        25         25
Vancouver                 22     22       22        22         22

In [ ]:
city_loca=[]
for city in list(df_map.groupby('City').count().index):
    geolocator = Nominatim(user_agent='Markov_Applied_DS')
    loca = geolocator.geocode(city)
    city_loca.append([city, loca.longitude, loca.latitude])
    #time.sleep(2.0)

city_loca

[['Bengaluru', 77.5912997, 12.9791198],
 ['San Francisco', -122.4199061, 37.7790262],
 ['Seoul', 126.9782914, 37.5666791],
 ['Vancouver', -123.1139529, 49.2608724]]

In [ ]:
df_city = pd.DataFrame(data=city_loca, columns=['City','Longitude', 'Latitude'])
df_city

City   Longitude   Latitude
0      Bengaluru   77.591300  12.979120
1  San Francisco -122.419906  37.779026
2          Seoul  126.978291  37.566679
3      Vancouver -123.113953  49.260872

In [ ]:
city_map = folium.Map(location = [0,0], zoom_start = 2)

#add markers to the cities
for lat, lng, label in zip(df_city['Latitude'], df_city['Longitude'], df_city['City']):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(city_map) 
         
city_map

## Neighbourhoods Maps

In [ ]:
#test get city lat
df_city.loc[df_city['City']=="San Francisco",'Latitude'].values[0]

37.7790262

In [ ]:
def generate_map (city, zoom):

    map = folium.Map(location=[df_city.loc[df_city['City']==city,'Latitude'].values[0],df_city.loc[df_city['City']==city,'Longitude'].values[0]], zoom_start=zoom)
    #add markers to the cities
    for lat, lng, label in zip(df_map.loc[df_map['City']==city,'Latitude'], df_map.loc[df_map['City']==city,'Longitude'], df_map.loc[df_map['City']==city,'Neighbourhood']):
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7).add_to(map)

    return map

In [ ]:
map_blr = generate_map('Bengaluru', 11)
map_blr

In [ ]:
map_sul = generate_map('Seoul', 11)
map_sul

In [ ]:
map_vnc = generate_map('Vancouver', 11)
map_vnc

In [ ]:
map_sfr = generate_map('San Francisco', 12)
map_sfr

# **5. Foursquare Location Services API**

## Getting Venues from Foursquare

In [ ]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100

#### API Test Request

In [ ]:
test_lat = '30.0492'
test_lng = '30.9762'
test_radius = 1000

In [ ]:
test_url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    test_lat, 
    test_lng, 
    test_radius, 
    LIMIT)

In [ ]:
requests.get(test_url).text

'{"meta":{"code":200,"requestId":"611a89518ea5fd26d8160c70"},"response":{"headerLocation":"Current map view","headerFullLocation":"Current map view","headerLocationGranularity":"unknown","totalResults":4,"suggestedBounds":{"ne":{"lat":30.058200009000007,"lng":30.986578060571667},"sw":{"lat":30.04019999099999,"lng":30.96582193942833}},"groups":[{"type":"Recommended Places","name":"recommended","items":[{"reasons":{"count":0,"items":[{"summary":"This spot is popular","type":"general","reasonName":"globalInteractionReason"}]},"venue":{"id":"590e2bec8134880da52d4dbc","name":"Seven Eleven Zayed","location":{"address":"The Address Compound","lat":30.044921124658863,"lng":30.981217245629242,"labeledLatLngs":[{"label":"display","lat":30.044921124658863,"lng":30.981217245629242}],"distance":678,"cc":"EG","city":"El shiekh Zayed","state":"Giza Governorate","country":"مصر","formattedAddress":["The Address Compound","El shiekh Zayed","Giza Governorate","مصر"]},"categories":[{"id":"4bf58dd8d48988d1

In [ ]:
requests.get(test_url).json()

{'meta': {'code': 200, 'requestId': '611a895748f0cd013ad655bd'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-590e2bec8134880da52d4dbc-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d175941735',
         'name': 'Gym / Fitness Center',
         'pluralName': 'Gyms or Fitness Centers',
         'primary': True,
         'shortName': 'Gym / Fitness'}],
       'id': '590e2bec8134880da52d4dbc',
       'location': {'address': 'The Address Compound',
        'cc': 'EG',
        'city': 'El shiekh Zayed',
        'country': 'مصر',
        'distance': 678,
        'formattedAddress': ['The Address Compound',
         'El shiekh Zayed',
         'Giza Governorate',
         'مصر'],
        'labeledLatL

In [ ]:
requests.get(test_url).json()['response']

{'groups': [{'items': [{'reasons': {'count': 0,
      'items': [{'reasonName': 'globalInteractionReason',
        'summary': 'This spot is popular',
        'type': 'general'}]},
     'referralId': 'e-0-590e2bec8134880da52d4dbc-0',
     'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_',
         'suffix': '.png'},
        'id': '4bf58dd8d48988d175941735',
        'name': 'Gym / Fitness Center',
        'pluralName': 'Gyms or Fitness Centers',
        'primary': True,
        'shortName': 'Gym / Fitness'}],
      'id': '590e2bec8134880da52d4dbc',
      'location': {'address': 'The Address Compound',
       'cc': 'EG',
       'city': 'El shiekh Zayed',
       'country': 'مصر',
       'distance': 678,
       'formattedAddress': ['The Address Compound',
        'El shiekh Zayed',
        'Giza Governorate',
        'مصر'],
       'labeledLatLngs': [{'label': 'display',
         'lat': 30.044921124658863,
         'lng': 30.981217245629242}]

In [ ]:
requests.get(test_url).json()['response']['groups']

[{'items': [{'reasons': {'count': 0,
     'items': [{'reasonName': 'globalInteractionReason',
       'summary': 'This spot is popular',
       'type': 'general'}]},
    'referralId': 'e-0-590e2bec8134880da52d4dbc-0',
    'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_',
        'suffix': '.png'},
       'id': '4bf58dd8d48988d175941735',
       'name': 'Gym / Fitness Center',
       'pluralName': 'Gyms or Fitness Centers',
       'primary': True,
       'shortName': 'Gym / Fitness'}],
     'id': '590e2bec8134880da52d4dbc',
     'location': {'address': 'The Address Compound',
      'cc': 'EG',
      'city': 'El shiekh Zayed',
      'country': 'مصر',
      'distance': 678,
      'formattedAddress': ['The Address Compound',
       'El shiekh Zayed',
       'Giza Governorate',
       'مصر'],
      'labeledLatLngs': [{'label': 'display',
        'lat': 30.044921124658863,
        'lng': 30.981217245629242}],
      'lat': 30.044921124658863,


In [ ]:
requests.get(test_url).json()['response']['groups'][0]['items']

[{'reasons': {'count': 0,
   'items': [{'reasonName': 'globalInteractionReason',
     'summary': 'This spot is popular',
     'type': 'general'}]},
  'referralId': 'e-0-590e2bec8134880da52d4dbc-0',
  'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_',
      'suffix': '.png'},
     'id': '4bf58dd8d48988d175941735',
     'name': 'Gym / Fitness Center',
     'pluralName': 'Gyms or Fitness Centers',
     'primary': True,
     'shortName': 'Gym / Fitness'}],
   'id': '590e2bec8134880da52d4dbc',
   'location': {'address': 'The Address Compound',
    'cc': 'EG',
    'city': 'El shiekh Zayed',
    'country': 'مصر',
    'distance': 678,
    'formattedAddress': ['The Address Compound',
     'El shiekh Zayed',
     'Giza Governorate',
     'مصر'],
    'labeledLatLngs': [{'label': 'display',
      'lat': 30.044921124658863,
      'lng': 30.981217245629242}],
    'lat': 30.044921124658863,
    'lng': 30.981217245629242,
    'state': 'Giza Governorate

In [ ]:
requests.get(test_url).json()['response']['groups'][0]['items'][0]['venue']['name']

'Seven Eleven Zayed'

In [ ]:
requests.get(test_url).json()['response']['groups'][0]['items'][0]['venue']['location']

{'address': 'The Address Compound',
 'cc': 'EG',
 'city': 'El shiekh Zayed',
 'country': 'مصر',
 'distance': 678,
 'formattedAddress': ['The Address Compound',
  'El shiekh Zayed',
  'Giza Governorate',
  'مصر'],
 'labeledLatLngs': [{'label': 'display',
   'lat': 30.044921124658863,
   'lng': 30.981217245629242}],
 'lat': 30.044921124658863,
 'lng': 30.981217245629242,
 'state': 'Giza Governorate'}

In [ ]:
requests.get(test_url).json()['response']['groups'][0]['items'][0]['venue']['categories'][0]['name']

'Gym / Fitness Center'

#### API Venues Request

In [ ]:
df_neigh = pd.read_excel("Neighbourhoods_Geolocations_v3.xlsx")
df_neigh

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...  14.286750  120.944712
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

In [ ]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000): #names: City Neighbourhoods
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)  #Neighbourhoods name
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        if (len(results)==0):
            print('0')
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results]) #v loops over items "venues"

    print("Venues list ", venues_list)   #list of Venues for all Neighbourhoods of the City
    print("Number of Neighbourhoods at the City ", len(venues_list))

    nearby_venues = pd.DataFrame([venue for neigh in venues_list for venue in neigh])
    # venues_list : list of lists of tubles "list of neighbourhoods, of list of venues, of tuble of venue data"
    nearby_venues.columns = ['Neighbourhood',
                             'Neighbourhood Latitude',
                             'Neighbourhood Longitude',
                             'Venue',
                             'Venue Latitude',
                             'Venue Longitude',
                             'Venue Category']

    return(nearby_venues)

In [ ]:
df_blrvenues = getNearbyVenues(df_neigh.loc[df_neigh['City']=='Bengaluru', 'Neighbourhood'],
                               df_neigh.loc[df_neigh['City']=='Bengaluru', 'Latitude'],
                               df_neigh.loc[df_neigh['City']=='Bengaluru', 'Longitude'], 1000)

Kempegowda
Chowdeshwari
Attur
Yelahanka Satellite Town
Jakkur
Thanisandra
Byatarayanapura
Kodigehalli
Vidyaranyapura
Doddabommasandra
Kuvempu Nagar
Shettyhalli
0
Mallasandra
Bagalagunte
T-Dasarahalli
Jalahalli
J.P.Park
Radhakrishna Temple
Sanjay Nagar
Ganga Nagar
Hebbal
Vishwanathnagenahalli
Nagavara
HBR Layout
Horamavu
Ramamurthy Nagar
Banaswadi
Kammanahalli
Kacharakanahalli
Kadugondanahalli
Kushal Nagar
Kavalbyrasandra
Manorayanapalya
Gangenahalli
Aramane Nagar
Mathikere
Yeshwanthpur
H.M.T
Chokkasandra
0
Dodda Bidarkallu
0
Peenya Industrial Area
Lakshmidevi Nagar
Nandini Layout
Marappana Palya
Malleshwaram
Jayachamarajendra Nagar
Devarajeevanahalli
Muneshwara Nagar
Lingarajapuram
Benniganahalli
Vijanapura
K.R.Puram
Basavanapura
0
Hoodi
Devasandra
A.Narayanapura
C.V.Raman Nagar
Hosathippasandra
Maruthiseva Nagar
Sagayapuram
S.K.Garden
Ramaswamy Palya
Jayamahal
Rajamahal
Kadumalleshwara
0
Subramanya Nagar
Nagapura
0
Mahalakshmipuram
Laggere
Rajagopala Nagar
0
Hegganahalli
Herohalli
Kot

In [ ]:
df_blrvenues

Neighbourhood  ...                 Venue Category
0       Kempegowda  ...  Vegetarian / Vegan Restaurant
1       Kempegowda  ...                           Lake
2       Kempegowda  ...                     Food Truck
3       Kempegowda  ...           Fast Food Restaurant
4     Chowdeshwari  ...                 Ice Cream Shop
...            ...  ...                            ...
4995   Hemmigepura  ...  Vegetarian / Vegan Restaurant
4996   Hemmigepura  ...                  Big Box Store
4997   Hemmigepura  ...                          Diner
4998   Hemmigepura  ...              Indian Restaurant
4999   Hemmigepura  ...                    Auto Garage

[5000 rows x 7 columns]

In [ ]:
df_sulvenues = getNearbyVenues(df_neigh.loc[df_neigh['City']=='Seoul', 'Neighbourhood'],
                               df_neigh.loc[df_neigh['City']=='Seoul', 'Latitude'],
                               df_neigh.loc[df_neigh['City']=='Seoul', 'Longitude'], 1000)

Dobong-gu
Dongdaemun-gu
Dongjak-gu
Eunpyeong-gu
Gangbuk-gu
Gangdong-gu
Gangnam-gu
Gangseo-gu
Geumcheon-gu
Guro-gu
Gwanak-gu
Gwangjin-gu
Jongno-gu
Jung-gu
Jungnang-gu
Mapo-gu
Nowon-gu
Seocho-gu
Seodaemun-gu
Seongbuk-gu
Seongdong-gu
Songpa-gu
Yangcheon-gu
Yeongdeungpo-gu
Yongsan-gu
Venues list  [[('Dobong-gu', 37.6911425, 127.045241, '도봉산 입구', 37.68882885885845, 127.04547694251437, 'Trail'), ('Dobong-gu', 37.6911425, 127.045241, '서울창포원', 37.685423078420506, 127.04809219139601, 'Park'), ('Dobong-gu', 37.6911425, 127.045241, '국립공원 북한산 생태탐방원', 37.687255, 127.035068, 'Resort'), ('Dobong-gu', 37.6911425, 127.045241, '도봉산 탐방지원센터', 37.686269790295384, 127.03605288061547, 'Trail'), ('Dobong-gu', 37.6911425, 127.045241, 'PARIS BAGUETTE', 37.683948387163234, 127.04593045772125, 'Bakery'), ('Dobong-gu', 37.6911425, 127.045241, '도봉산역 광역환승센터', 37.69001145295688, 127.04562893350203, 'Bus Stop'), ('Dobong-gu', 37.6911425, 127.045241, '다락원 체육공원', 37.691006, 127.047424, 'Gym'), ('Dobong-gu', 37.6911425, 

In [ ]:
df_sulvenues

Neighbourhood  Neighbourhood Latitude  ...  Venue Longitude      Venue Category
0        Dobong-gu               37.691142  ...       127.045477               Trail
1        Dobong-gu               37.691142  ...       127.048092                Park
2        Dobong-gu               37.691142  ...       127.035068              Resort
3        Dobong-gu               37.691142  ...       127.036053               Trail
4        Dobong-gu               37.691142  ...       127.045930              Bakery
...            ...                     ...  ...              ...                 ...
1223    Yongsan-gu               37.553098  ...       126.967701            Building
1224    Yongsan-gu               37.553098  ...       126.975080         Coffee Shop
1225    Yongsan-gu               37.553098  ...       126.967922  Seafood Restaurant
1226    Yongsan-gu               37.553098  ...       126.971476              Bakery
1227    Yongsan-gu               37.553098  ...       126.977157   Korean Restaurant

[1228 rows x 7 columns]

In [ ]:
df_vncvenues = getNearbyVenues(df_neigh.loc[df_neigh['City']=='Vancouver', 'Neighbourhood'],
                               df_neigh.loc[df_neigh['City']=='Vancouver', 'Latitude'],
                               df_neigh.loc[df_neigh['City']=='Vancouver', 'Longitude'], 1000)

Arbutus Ridge
Downtown
Dunbar-Southlands
Fairview
Grandview-Woodland
Hastings-Sunrise
Kensington-Cedar Cottage
Kerrisdale
Killarney
Kitsilano
Marpole
Mount Pleasant
Oakridge
Renfrew-Collingwood
Riley Park
Shaughnessy
South Cambie
Strathcona
Sunset
Victoria-Fraserview
West End
West Point Grey
Venues list  [[('Arbutus Ridge', 49.2409677, -123.1670008, 'Butter Baked Goods', 49.242209327685536, -123.17038089631828, 'Bakery'), ('Arbutus Ridge', 49.2409677, -123.1670008, "Minerva's Pizza & Steakhouse", 49.234674420009775, -123.16177360236595, 'Italian Restaurant'), ('Arbutus Ridge', 49.2409677, -123.1670008, 'Bufala', 49.23743420766769, -123.1555764422288, 'Pizza Place'), ('Arbutus Ridge', 49.2409677, -123.1670008, 'Starbucks', 49.234263, -123.160344, 'Coffee Shop'), ('Arbutus Ridge', 49.2409677, -123.1670008, 'Secret Garden Tea Company', 49.235969630822524, -123.15563690455153, 'Tea Room'), ('Arbutus Ridge', 49.2409677, -123.1670008, 'White Spot', 49.23763447335214, -123.15546667190972, 'Bu

In [ ]:
df_vncvenues

Neighbourhood  ...        Venue Category
0       Arbutus Ridge  ...                Bakery
1       Arbutus Ridge  ...    Italian Restaurant
2       Arbutus Ridge  ...           Pizza Place
3       Arbutus Ridge  ...           Coffee Shop
4       Arbutus Ridge  ...              Tea Room
...               ...  ...                   ...
1437  West Point Grey  ...           Coffee Shop
1438  West Point Grey  ...     Indian Restaurant
1439  West Point Grey  ...           Dry Cleaner
1440  West Point Grey  ...      Sushi Restaurant
1441  West Point Grey  ...  Gym / Fitness Center

[1442 rows x 7 columns]

In [ ]:
df_sfrvenues = getNearbyVenues(df_neigh.loc[df_neigh['City']=='San Francisco', 'Neighbourhood'],
                               df_neigh.loc[df_neigh['City']=='San Francisco', 'Latitude'],
                               df_neigh.loc[df_neigh['City']=='San Francisco', 'Longitude'], 1000)

Alamo Square
Anza Vista
Ashbury Heights
Balboa Park
Balboa Terrace
Bayview
Belden Place
Bernal Heights
Buena Vista
Butchertown (Old and New)
Castro
Cathedral Hill
Cayuga Terrace
China Basin
Chinatown
Civic Center
Clarendon Heights
Cole Valley
Corona Heights
Cow Hollow
Crocker-Amazon
Design District
Diamond Heights
Dogpatch
Dolores Heights
Duboce Triangle
Embarcadero
Eureka Valley
Excelsior
Fillmore
Financial District
Financial District South
Fisherman's Wharf
Forest Hill
Forest Knolls
Glen Park
Golden Gate Heights
Haight-Ashbury
Hayes Valley
Hunters Point
India Basin
Ingleside
Ingleside Terraces
Inner Sunset
Irish Hill
Islais Creek
Jackson Square
Japantown
Jordan Park
Laguna Honda
Lake Street
Lakeside
Lakeshore
Laurel Heights
Lincoln Manor
Little Hollywood
Little Russia
Little Saigon
Lone Mountain
Lower Haight
Lower Pacific Heights
Lower Nob Hill
Marina District
Merced Heights
Merced Manor
0
Midtown Terrace
Mid-Market
Miraloma Park
Mission Bay
Mission District
Mission Dolores
Mission T

In [ ]:
df_sfrvenues

Neighbourhood  Neighbourhood Latitude  ...  Venue Longitude     Venue Category
0      Alamo Square               37.776360  ...      -122.434634               Park
1      Alamo Square               37.776360  ...      -122.435740            Dog Run
2      Alamo Square               37.776360  ...      -122.433389      Historic Site
3      Alamo Square               37.776360  ...      -122.436239     Sandwich Place
4      Alamo Square               37.776360  ...      -122.437835          Rock Club
...             ...                     ...  ...              ...                ...
8127  Westwood Park               49.277466  ...      -122.784265       Home Service
8128  Westwood Park               49.277466  ...      -122.785276      Shopping Mall
8129  Westwood Park               49.277466  ...      -122.788473        Pizza Place
8130  Westwood Park               49.277466  ...      -122.785988  Korean Restaurant
8131  Westwood Park               49.277466  ...      -122.788947        Coffee Shop

[8132 rows x 7 columns]

#### Save output DataFrames in one Excel File

In [ ]:
#save dataframes to an excel file
with pd.ExcelWriter('Neighbourhoods_with_Venues.xlsx') as writer:  
    df_blrvenues.to_excel(writer, sheet_name='blrvenues', index=False)
    df_sulvenues.to_excel(writer, sheet_name='sulvenues', index=False)
    df_vncvenues.to_excel(writer, sheet_name='vncvenues', index=False)
    df_sfrvenues.to_excel(writer, sheet_name='sfrvenues', index=False)

## Most common Venue Categories at each Neighbourhood

In [ ]:
#one hot encoding for venues categories
def onehot_df(df_venues):
    df_onehot = pd.get_dummies(df_venues[['Venue Category']], prefix="", prefix_sep="")
    df_onehot['Neighbourhood'] = df_venues['Neighbourhood'] 
    # move neighborhood column to the first column
    fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
    df_onehot = df_onehot[fixed_columns]

    return df_onehot

In [ ]:
#most common venues per neighboarhood
def return_most_common_venues(row, num_top_venues):  #row=neigh row after groupby "blr_grouped"
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [ ]:
#sort top 20 venue categories
def sorted_dataframe(df_grouped):
    num_top_venues = 20

    indicators = ['st', 'nd', 'rd']

    # create dynamic list with columns' names of top venues
    columns = ['Neighbourhood']
    for ind in range(num_top_venues):
        try:
            columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))  #1st Most Common Venue & 2nd & 3rd
        except:
            columns.append('{}th Most Common Venue'.format(ind+1))   #4th & more

    # create a new dataframe
    df_venues_sorted = pd.DataFrame(columns=columns)
    df_venues_sorted['Neighbourhood'] = df_grouped['Neighbourhood']

    for ind in range(df_grouped.shape[0]):   #number of neighbourhoods
        df_venues_sorted.iloc[ind, 1:] = return_most_common_venues(df_grouped.iloc[ind, :], num_top_venues)

    return df_venues_sorted

#### Bengaluru Venues

In [ ]:
df_blrvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="blrvenues")
df_blrvenues.head()

Neighbourhood  ...                 Venue Category
0    Kempegowda  ...  Vegetarian / Vegan Restaurant
1    Kempegowda  ...                           Lake
2    Kempegowda  ...                     Food Truck
3    Kempegowda  ...           Fast Food Restaurant
4  Chowdeshwari  ...        South Indian Restaurant

[5 rows x 7 columns]

In [ ]:
df_blrvenues.shape

(5052, 7)

In [ ]:
blr_onehot = onehot_df(df_blrvenues)
blr_onehot.head()

Neighbourhood  ATM  Accessories Store  ...  Wine Shop  Women's Store  Yoga Studio
0    Kempegowda    0                  0  ...          0              0            0
1    Kempegowda    0                  0  ...          0              0            0
2    Kempegowda    0                  0  ...          0              0            0
3    Kempegowda    0                  0  ...          0              0            0
4  Chowdeshwari    0                  0  ...          0              0            0

[5 rows x 260 columns]

In [ ]:
blr_onehot.shape

(5052, 260)

In [ ]:
blr_grouped = blr_onehot.groupby('Neighbourhood').sum().reset_index()
blr_grouped.head()

Neighbourhood  ATM  ...  Women's Store  Yoga Studio
0        A.Narayanapura    0  ...              0            0
1               Adugodi    0  ...              0            0
2                Agaram    0  ...              0            0
3  Agrahara Dasarahalli    0  ...              0            0
4             Anjanapur    0  ...              0            0

[5 rows x 260 columns]

In [ ]:
blr_grouped.shape

(189, 260)

In [ ]:
#test function
blr_grouped.iloc[0, :]

Neighbourhood        A.Narayanapura
ATM                               0
Accessories Store                 0
Afghan Restaurant                 0
Airport Terminal                  0
                          ...      
Volleyball Court                  0
Wine Bar                          0
Wine Shop                         0
Women's Store                     0
Yoga Studio                       0
Name: 0, Length: 260, dtype: object

In [ ]:
#test function
(blr_grouped.iloc[0, :]).iloc[1:]

ATM                    0
Accessories Store      0
Afghan Restaurant      0
Airport Terminal       0
American Restaurant    0
                      ..
Volleyball Court       0
Wine Bar               0
Wine Shop              0
Women's Store          0
Yoga Studio            0
Name: 0, Length: 259, dtype: object

In [ ]:
#test function
((blr_grouped.iloc[0, :]).iloc[1:]).sort_values(ascending=False)

Indian Restaurant                  6
Fast Food Restaurant               3
Department Store                   3
Snack Place                        2
Pizza Place                        2
                                  ..
Motorcycle Shop                    0
Monument / Landmark                0
Molecular Gastronomy Restaurant    0
Modern European Restaurant         0
ATM                                0
Name: 0, Length: 259, dtype: object

In [ ]:
#test function
(((blr_grouped.iloc[0, :]).iloc[1:]).sort_values(ascending=False)).index.values[:20]

array(['Indian Restaurant', 'Fast Food Restaurant', 'Department Store',
       'Snack Place', 'Pizza Place', 'Steakhouse', 'Bus Station', 'Café',
       'New American Restaurant', 'Sporting Goods Shop', 'Donut Shop',
       'Clothing Store', 'Italian Restaurant', 'Coffee Shop',
       'Shopping Mall', 'Pharmacy', 'Convenience Store', 'Bowling Alley',
       'Bus Stop', 'Flea Market'], dtype=object)

In [ ]:
#test complete function
return_most_common_venues(blr_grouped.iloc[0, :], 20) #first neigh

array(['Indian Restaurant', 'Fast Food Restaurant', 'Department Store',
       'Snack Place', 'Pizza Place', 'Steakhouse', 'Bus Station', 'Café',
       'New American Restaurant', 'Sporting Goods Shop', 'Donut Shop',
       'Clothing Store', 'Italian Restaurant', 'Coffee Shop',
       'Shopping Mall', 'Pharmacy', 'Convenience Store', 'Bowling Alley',
       'Bus Stop', 'Flea Market'], dtype=object)

In [ ]:
blr_venues_sorted = sorted_dataframe(blr_grouped)
blr_venues_sorted.head()

Neighbourhood  ... 20th Most Common Venue
0        A.Narayanapura  ...            Flea Market
1               Adugodi  ...          Movie Theater
2                Agaram  ...         Ice Cream Shop
3  Agrahara Dasarahalli  ...      Food & Drink Shop
4             Anjanapur  ...    Dumpling Restaurant

[5 rows x 21 columns]

In [ ]:
blr_venues_sorted.shape

(189, 21)

#### Seoul Venues

In [ ]:
df_sulvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="sulvenues")
sul_onehot = onehot_df(df_sulvenues)
sul_onehot.head()

Neighbourhood  Airport Service  ...  Wine Bar  Zoo
0     Dobong-gu                0  ...         0    0
1     Dobong-gu                0  ...         0    0
2     Dobong-gu                0  ...         0    0
3     Dobong-gu                0  ...         0    0
4     Dobong-gu                0  ...         0    0

[5 rows x 174 columns]

In [ ]:
sul_grouped=sul_onehot.groupby('Neighbourhood').sum().reset_index()
sul_grouped.head()

Neighbourhood  Airport Service  ...  Wine Bar  Zoo
0      Dobong-gu                0  ...         0    0
1  Dongdaemun-gu                0  ...         0    0
2     Dongjak-gu                0  ...         0    0
3   Eunpyeong-gu                0  ...         0    0
4     Gangbuk-gu                0  ...         0    0

[5 rows x 174 columns]

In [ ]:
sul_venues_sorted = sorted_dataframe(sul_grouped)
sul_venues_sorted.head()

Neighbourhood  ... 20th Most Common Venue
0      Dobong-gu  ...             Food Truck
1  Dongdaemun-gu  ...     Golf Driving Range
2     Dongjak-gu  ...                    Bar
3   Eunpyeong-gu  ...          Historic Site
4     Gangbuk-gu  ...            Event Space

[5 rows x 21 columns]

#### Vancouver Venues

In [ ]:
df_vncvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="vncvenues")
vnc_onehot = onehot_df(df_vncvenues)
vnc_onehot.head()

Neighbourhood  Accessories Store  ...  Women's Store  Yoga Studio
0  Arbutus Ridge                  0  ...              0            0
1  Arbutus Ridge                  0  ...              0            0
2  Arbutus Ridge                  0  ...              0            0
3  Arbutus Ridge                  0  ...              0            0
4  Arbutus Ridge                  0  ...              0            0

[5 rows x 229 columns]

In [ ]:
vnc_grouped = vnc_onehot.groupby('Neighbourhood').sum().reset_index()
vnc_grouped.head()

Neighbourhood  Accessories Store  ...  Women's Store  Yoga Studio
0       Arbutus Ridge                  0  ...              0            0
1            Downtown                  0  ...              0            1
2   Dunbar-Southlands                  0  ...              0            0
3            Fairview                  0  ...              1            1
4  Grandview-Woodland                  0  ...              0            0

[5 rows x 229 columns]

In [ ]:
vnc_venues_sorted = sorted_dataframe(vnc_grouped)
vnc_venues_sorted.head()

Neighbourhood  ... 20th Most Common Venue
0       Arbutus Ridge  ...               Bus Stop
1            Downtown  ...         Cosmetics Shop
2   Dunbar-Southlands  ...         Ice Cream Shop
3            Fairview  ...       Toy / Game Store
4  Grandview-Woodland  ...       Tapas Restaurant

[5 rows x 21 columns]

#### San Francisco Venues

In [ ]:
df_sfrvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="sfrvenues")
sfr_onehot = onehot_df(df_sfrvenues)
sfr_onehot.head()

Neighbourhood  Accessories Store  ...  Yoga Studio  Zoo Exhibit
0  Alamo Square                  0  ...            0            0
1  Alamo Square                  0  ...            0            0
2  Alamo Square                  0  ...            0            0
3  Alamo Square                  0  ...            0            0
4  Alamo Square                  0  ...            0            0

[5 rows x 399 columns]

In [ ]:
sfr_grouped = sfr_onehot.groupby('Neighbourhood').sum().reset_index()
sfr_grouped.head()

Neighbourhood  Accessories Store  ...  Yoga Studio  Zoo Exhibit
0     Alamo Square                  1  ...            2            0
1       Anza Vista                  0  ...            2            0
2  Ashbury Heights                  0  ...            0            0
3      Balboa Park                  0  ...            0            0
4   Balboa Terrace                  0  ...            0            0

[5 rows x 399 columns]

In [ ]:
sfr_venues_sorted = sorted_dataframe(sfr_grouped)
sfr_venues_sorted.head()

Neighbourhood  ... 20th Most Common Venue
0     Alamo Square  ...               Wine Bar
1       Anza Vista  ...                 Market
2  Ashbury Heights  ...             Food Truck
3      Balboa Park  ...                   Café
4   Balboa Terrace  ...    Japanese Restaurant

[5 rows x 21 columns]

#### Save output DataFrames in one Excel File

In [ ]:
#save one hot venues dataframes to an excel file
with pd.ExcelWriter('Neighbourhoods_onehot_Venues_Categories.xlsx') as writer:  
    blr_grouped.to_excel(writer, sheet_name='blrvenues', index=False)
    sul_grouped.to_excel(writer, sheet_name='sulvenues', index=False)
    vnc_grouped.to_excel(writer, sheet_name='vncvenues', index=False)
    sfr_grouped.to_excel(writer, sheet_name='sfrvenues', index=False)

#save most common venues dataframes to an excel file
with pd.ExcelWriter('Neighbourhoods_most_common_Venues_Categories.xlsx') as writer:  
    blr_venues_sorted.to_excel(writer, sheet_name='blrvenues', index=False)
    sul_venues_sorted.to_excel(writer, sheet_name='sulvenues', index=False)
    vnc_venues_sorted.to_excel(writer, sheet_name='vncvenues', index=False)
    sfr_venues_sorted.to_excel(writer, sheet_name='sfrvenues', index=False)

# **6. Individual Clustering**

In [ ]:
def map_city_clusters(df_merged, longitude, latitude):
    # create map
    map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)
    
    colors = ['#ff0000', '#8000ff', '#3c68f9', '#d4dd80', '#f6be68', '#ff964f', '#2adddd', '#b2f396']  

    # add markers to the map
    for lat, lon, neigh, cluster in zip(df_merged['Latitude'], df_merged['Longitude'], df_merged['Neighbourhood'], df_merged['Cluster Labels']):
        label = str(neigh) + ' (Cluster ' + str(cluster) + ')'
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            color=colors[cluster],
            fill=True,
            fill_color=colors[cluster],
            fill_opacity=0.7).add_to(map_clusters)

    return map_clusters

In [ ]:
df_neigh = pd.read_excel("Neighbourhoods_Geolocations_v3.xlsx")
df_neigh

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
359               West Portal  San Francisco  ...  37.741141 -122.465634
360          Western Addition  San Francisco  ...  37.779559 -122.429810
361        Westwood Highlands  San Francisco  ...  14.286750  120.944712
362             Westwood Park  San Francisco  ...  49.277466 -122.777594
363               Yerba Buena  San Francisco  ...  -6.991968  -78.373201

[364 rows x 6 columns]

## Bengaluru Map

In [ ]:
blr_grouped = pd.read_excel("/content/Neighbourhoods_onehot_Venues_Categories.xlsx", sheet_name="blrvenues")
blr_grouped

Neighbourhood  ATM  ...  Women's Store  Yoga Studio
0              A.Narayanapura    0  ...              0            0
1                     Adugodi    0  ...              0            0
2                      Agaram    0  ...              0            0
3        Agrahara Dasarahalli    0  ...              0            0
4                   Anjanapur    0  ...              0            0
..                        ...  ...  ...            ...          ...
184            Vrushabhavathi    0  ...              0            0
185                  Yadiyuru    0  ...              0            0
186            Yelachenahalli    0  ...              0            0
187  Yelahanka Satellite Town    0  ...              0            0
188              Yeshwanthpur    0  ...              0            0

[189 rows x 260 columns]

In [ ]:
# set number of clusters
kclusters = 8

blr_grouped_clustering = blr_grouped.drop('Neighbourhood', axis=1)

# run k-means clustering
kmeans_blr = KMeans(n_clusters=kclusters, random_state=0).fit(blr_grouped_clustering)

# check cluster labels generated for each row in the dataframe
len(kmeans_blr.labels_)

189

In [ ]:
blr_merged = df_neigh.loc[df_neigh['City']=='Bengaluru']
blr_merged = blr_merged[blr_merged['Neighbourhood'].isin(blr_grouped['Neighbourhood'])].reset_index(drop=True)
blr_merged

Neighbourhood       City State Country   Latitude  Longitude
0                  Kempegowda  Bengaluru    KA   India  13.109018  77.601900
1                Chowdeshwari  Bengaluru    KA   India  12.925190  77.588020
2                       Attur  Bengaluru    KA   India  13.111482  77.563056
3    Yelahanka Satellite Town  Bengaluru    KA   India  13.089139  77.582717
4                      Jakkur  Bengaluru    KA   India  13.078474  77.606894
..                        ...        ...   ...     ...        ...        ...
184                 Gottigere  Bengaluru    KA   India  12.856532  77.587724
185               Konanakunte  Bengaluru    KA   India  12.879286  77.569753
186                 Anjanapur  Bengaluru    KA   India  12.854900  77.554300
187              Vasanthapura  Bengaluru    KA   India  12.889297  77.559552
188               Hemmigepura  Bengaluru    KA   India  12.931046  77.508580

[189 rows x 6 columns]

In [ ]:
# add clustering labels
blr_merged['Cluster Labels'] = kmeans_blr.labels_

# merge blr_merged with blr_venues_sorted to add latitude/longitude for each neighborhood
blr_merged = blr_merged.join(blr_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

blr_merged.head() # check the last columns!

Neighbourhood  ...       20th Most Common Venue
0                Kempegowda  ...  Eastern European Restaurant
1              Chowdeshwari  ...                      Brewery
2                     Attur  ...                  Event Space
3  Yelahanka Satellite Town  ...            Electronics Store
4                    Jakkur  ...            Electronics Store

[5 rows x 27 columns]

In [ ]:
blr_merged.shape

(189, 27)

In [ ]:
df_city.loc[df_city['City']=='Bengaluru', 'Longitude']

0    77.5913
Name: Longitude, dtype: float64

In [ ]:
blr_lng = df_city.loc[df_city['City']=='Bengaluru', 'Longitude'][0]
blr_lat = df_city.loc[df_city['City']=='Bengaluru', 'Latitude'][0]

In [ ]:
map_city_clusters(blr_merged, blr_lng, blr_lat)

In [ ]:
blr_merged.groupby('Cluster Labels').count()

Neighbourhood  ...  20th Most Common Venue
Cluster Labels                 ...                        
0                          90  ...                      90
1                          14  ...                      14
2                          11  ...                      11
3                           9  ...                       9
4                           7  ...                       7
5                          30  ...                      30
6                          23  ...                      23
7                           5  ...                       5

[8 rows x 26 columns]

## Bengaluru Clusters

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==0,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
4           Jakkur  ...       Electronics Store
7      Kodigehalli  ...             Event Space
8   Vidyaranyapura  ...             Flea Market
10   Kuvempu Nagar  ...       Electronics Store
13   T-Dasarahalli  ...             Event Space

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==1,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
6    Byatarayanapura  ...           Fishing Store
14         Jalahalli  ...       Electronics Store
28  Kadugondanahalli  ...       Electronics Store
45  Muneshwara Nagar  ...     Dumpling Restaurant
58        S.K.Garden  ...             Flea Market

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==2,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
30      Kavalbyrasandra  ...     Fried Chicken Joint
41      Marappana Palya  ...       Food & Drink Shop
42         Malleshwaram  ...          Clothing Store
54      C.V.Raman Nagar  ...           Bowling Alley
72   Dattathreya Temple  ...          Breakfast Spot
84            Jogupalya  ...             Pizza Place
85               Ulsoor  ...                Tea Room
104           Chickpete  ...              Food Truck
120         Marenahalli  ...            Cupcake Shop
133          Chamrajpet  ...      Dim Sum Restaurant
162            Madiwala  ...             Fish Market

[11 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==3,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
9    Doddabommasandra  ...          Farmers Market
25          Banaswadi  ...                    Food
33      Aramane Nagar  ...               Juice Bar
46     Lingarajapuram  ...            Dance Studio
112     Shanthi Nagar  ...            Hockey Arena

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==4,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...       20th Most Common Venue
18    Ganga Nagar  ...                     Hospital
66   Hegganahalli  ...  Eastern European Restaurant
148     Sri Nagar  ...                 Burger Joint
155    Katriguppe  ...                  Flower Shop
158      Yadiyuru  ...                   Donut Shop

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==5,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...       20th Most Common Venue
0                 Kempegowda  ...  Eastern European Restaurant
3   Yelahanka Satellite Town  ...            Electronics Store
21                  Nagavara  ...   Financial or Legal Service
24          Ramamurthy Nagar  ...                  Event Space
27          Kacharakanahalli  ...                  Flea Market

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==6,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
1   Chowdeshwari  ...                 Brewery
2          Attur  ...             Event Space
5    Thanisandra  ...     Dumpling Restaurant
11   Mallasandra  ...             Event Space
12   Bagalagunte  ...          Cosmetics Shop

[5 rows x 22 columns]

In [ ]:
blr_merged.loc[blr_merged['Cluster Labels']==7,blr_merged.columns[[0] + list(range(6, blr_merged.shape[1]))]].head()

Neighbourhood  ...          20th Most Common Venue
36                H.M.T  ...                       Bookstore
49            K.R.Puram  ...               Electronics Store
55     Hosathippasandra  ...  Multicuisine Indian Restaurant
164          HSR Layout  ...                  Sandwich Place
171  Kumaraswamy Layout  ...                     Fish Market

[5 rows x 22 columns]

## Seoul Map

In [ ]:
sul_grouped = pd.read_excel("/content/Neighbourhoods_onehot_Venues_Categories.xlsx", sheet_name="sulvenues")
sul_grouped

Neighbourhood  Airport Service  ...  Wine Bar  Zoo
0         Dobong-gu                0  ...         0    0
1     Dongdaemun-gu                0  ...         0    0
2        Dongjak-gu                0  ...         0    0
3      Eunpyeong-gu                0  ...         0    0
4        Gangbuk-gu                0  ...         0    0
5       Gangdong-gu                0  ...         0    0
6        Gangnam-gu                1  ...         0    0
7        Gangseo-gu                0  ...         0    0
8      Geumcheon-gu                0  ...         0    0
9           Guro-gu                0  ...         0    0
10        Gwanak-gu                0  ...         0    0
11      Gwangjin-gu                0  ...         0    1
12        Jongno-gu                0  ...         0    0
13          Jung-gu                0  ...         0    0
14      Jungnang-gu                0  ...         0    0
15          Mapo-gu                0  ...         0    0
16         Nowon-gu                0  ...         0    0
17        Seocho-gu                0  ...         0    0
18     Seodaemun-gu                0  ...         0    0
19      Seongbuk-gu                0  ...         1    0
20     Seongdong-gu                0  ...         0    1
21        Songpa-gu                0  ...         0    0
22     Yangcheon-gu                0  ...         0    0
23  Yeongdeungpo-gu                0  ...         1    0
24       Yongsan-gu                0  ...         0    0

[25 rows x 174 columns]

In [ ]:
# set number of clusters
kclusters = 8

sul_grouped_clustering = sul_grouped.drop('Neighbourhood', axis=1)

# run k-means clustering
kmeans_sul = KMeans(n_clusters=kclusters, random_state=0).fit(sul_grouped_clustering)

# check cluster labels generated for each row in the dataframe
len(kmeans_sul.labels_)

25

In [ ]:
sul_merged = df_neigh.loc[df_neigh['City']=='Seoul']
sul_merged = sul_merged[sul_merged['Neighbourhood'].isin(sul_grouped['Neighbourhood'])].reset_index(drop=True)
sul_merged

Neighbourhood   City     State      Country   Latitude   Longitude
0         Dobong-gu  Seoul  Gyeonggi  South Korea  37.691142  127.045241
1     Dongdaemun-gu  Seoul  Gyeonggi  South Korea  37.597121  127.051987
2        Dongjak-gu  Seoul  Gyeonggi  South Korea  37.502973  126.980358
3      Eunpyeong-gu  Seoul  Gyeonggi  South Korea  37.582443  126.904544
4        Gangbuk-gu  Seoul  Gyeonggi  South Korea  37.638623  127.014857
5       Gangdong-gu  Seoul  Gyeonggi  South Korea  37.569501  127.177941
6        Gangnam-gu  Seoul  Gyeonggi  South Korea  37.517873  127.056772
7        Gangseo-gu  Seoul  Gyeonggi  South Korea  37.562975  126.821596
8      Geumcheon-gu  Seoul  Gyeonggi  South Korea  37.454686  126.894561
9           Guro-gu  Seoul  Gyeonggi  South Korea  37.503447  126.882509
10        Gwanak-gu  Seoul  Gyeonggi  South Korea  37.458128  126.952134
11      Gwangjin-gu  Seoul  Gyeonggi  South Korea  37.551698  127.089795
12        Jongno-gu  Seoul  Gyeonggi  South Korea  37.587520  126.969330
13          Jung-gu  Seoul  Gyeonggi  South Korea  37.687026  127.539751
14      Jungnang-gu  Seoul  Gyeonggi  South Korea  37.617416  127.091097
15          Mapo-gu  Seoul  Gyeonggi  South Korea  37.568302  126.897248
16         Nowon-gu  Seoul  Gyeonggi  South Korea  37.632972  127.075034
17        Seocho-gu  Seoul  Gyeonggi  South Korea  37.505486  127.005495
18     Seodaemun-gu  Seoul  Gyeonggi  South Korea  37.564786  126.962170
19      Seongbuk-gu  Seoul  Gyeonggi  South Korea  37.591487  126.998447
20     Seongdong-gu  Seoul  Gyeonggi  South Korea  37.543592  127.044740
21        Songpa-gu  Seoul  Gyeonggi  South Korea  37.477291  127.137189
22     Yangcheon-gu  Seoul  Gyeonggi  South Korea  37.520534  126.834419
23  Yeongdeungpo-gu  Seoul  Gyeonggi  South Korea  37.525389  126.926634
24       Yongsan-gu  Seoul  Gyeonggi  South Korea  37.553098  126.972613

In [ ]:
# add clustering labels
sul_merged['Cluster Labels'] = kmeans_sul.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
sul_merged = sul_merged.join(sul_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

sul_merged.head() # check the last columns!

Neighbourhood   City  ... 19th Most Common Venue 20th Most Common Venue
0      Dobong-gu  Seoul  ...      Electronics Store             Food Truck
1  Dongdaemun-gu  Seoul  ...       Asian Restaurant     Golf Driving Range
2     Dongjak-gu  Seoul  ...  Outdoors & Recreation                    Bar
3   Eunpyeong-gu  Seoul  ...             Food Court          Historic Site
4     Gangbuk-gu  Seoul  ...           Dessert Shop            Event Space

[5 rows x 27 columns]

In [ ]:
sul_merged.shape

(25, 27)

In [ ]:
df_city.loc[df_city['City']=='Seoul', 'Longitude']

2    126.978291
Name: Longitude, dtype: float64

In [ ]:
sul_lng = df_city.loc[df_city['City']=='Seoul', 'Longitude'][2]
sul_lat = df_city.loc[df_city['City']=='Seoul', 'Latitude'][2]

In [ ]:
map_city_clusters(sul_merged, sul_lng, sul_lat)

In [ ]:
sul_merged.groupby('Cluster Labels').count()

Neighbourhood  ...  20th Most Common Venue
Cluster Labels                 ...                        
0                           1  ...                       1
1                          14  ...                      14
2                           2  ...                       2
3                           1  ...                       1
4                           1  ...                       1
5                           3  ...                       3
6                           2  ...                       2
7                           1  ...                       1

[8 rows x 26 columns]

## Seoul Clusters

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==0,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
12     Jongno-gu               0  ...         Scenic Lookout           Burger Joint

[1 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==1,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
0     Dobong-gu               1  ...      Electronics Store             Food Truck
3  Eunpyeong-gu               1  ...             Food Court          Historic Site
4    Gangbuk-gu               1  ...           Dessert Shop            Event Space
5   Gangdong-gu               1  ...            Event Space      Elementary School
7    Gangseo-gu               1  ...                Dog Run               Dive Bar

[5 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==2,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
18  Seodaemun-gu               2  ...             Restaurant    Monument / Landmark
19   Seongbuk-gu               2  ...  Performing Arts Venue              Rock Club

[2 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==3,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
23  Yeongdeungpo-gu  ...                   Plaza

[1 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==4,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
20  Seongdong-gu               4  ...                 Lounge                    Zoo

[1 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==5,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
1  Dongdaemun-gu               5  ...       Asian Restaurant     Golf Driving Range
2     Dongjak-gu               5  ...  Outdoors & Recreation                    Bar
9        Guro-gu               5  ...        Bubble Tea Shop           Dessert Shop

[3 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==6,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
6     Gangnam-gu               6  ...     Chinese Restaurant                 Lounge
24    Yongsan-gu               6  ...                 Bakery             Restaurant

[2 rows x 22 columns]

In [ ]:
sul_merged.loc[sul_merged['Cluster Labels']==7,sul_merged.columns[[0] + list(range(6, sul_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
17     Seocho-gu               7  ...              Hotel Bar                  Hotel

[1 rows x 22 columns]

## Vancouver Map

In [ ]:
vnc_grouped = pd.read_excel("/content/Neighbourhoods_onehot_Venues_Categories.xlsx", sheet_name="vncvenues")
vnc_grouped

Neighbourhood  Accessories Store  ...  Women's Store  Yoga Studio
0              Arbutus Ridge                  0  ...              0            0
1                   Downtown                  0  ...              0            1
2          Dunbar-Southlands                  0  ...              0            0
3                   Fairview                  0  ...              1            1
4         Grandview-Woodland                  0  ...              0            0
5           Hastings-Sunrise                  0  ...              0            0
6   Kensington-Cedar Cottage                  0  ...              0            0
7                 Kerrisdale                  0  ...              0            0
8                  Killarney                  0  ...              0            0
9                  Kitsilano                  0  ...              0            4
10                   Marpole                  0  ...              0            0
11            Mount Pleasant                  0  ...              0            2
12                  Oakridge                  1  ...              2            0
13       Renfrew-Collingwood                  0  ...              0            0
14                Riley Park                  0  ...              0            0
15               Shaughnessy                  0  ...              1            0
16              South Cambie                  0  ...              0            0
17                Strathcona                  0  ...              0            0
18                    Sunset                  0  ...              0            0
19       Victoria-Fraserview                  0  ...              0            0
20                  West End                  0  ...              1            1
21           West Point Grey                  0  ...              0            1

[22 rows x 229 columns]

In [ ]:
# set number of clusters
kclusters = 8

vnc_grouped_clustering = vnc_grouped.drop('Neighbourhood', axis=1)

# run k-means clustering
kmeans_vnc = KMeans(n_clusters=kclusters, random_state=0).fit(vnc_grouped_clustering)

# check cluster labels generated for each row in the dataframe
len(kmeans_vnc.labels_)

22

In [ ]:
vnc_merged = df_neigh.loc[df_neigh['City']=='Vancouver']
vnc_merged = vnc_merged[vnc_merged['Neighbourhood'].isin(vnc_grouped['Neighbourhood'])].reset_index(drop=True)
vnc_merged

Neighbourhood       City State Country   Latitude   Longitude
0              Arbutus Ridge  Vancouver    BC  Canada  49.240968 -123.167001
1                   Downtown  Vancouver    BC  Canada  49.283393 -123.117456
2          Dunbar-Southlands  Vancouver    BC  Canada  49.253460 -123.185044
3                   Fairview  Vancouver    BC  Canada  49.264113 -123.126835
4         Grandview-Woodland  Vancouver    BC  Canada  49.270559 -123.067942
5           Hastings-Sunrise  Vancouver    BC  Canada  49.277594 -123.043920
6   Kensington-Cedar Cottage  Vancouver    BC  Canada  49.247632 -123.084207
7                 Kerrisdale  Vancouver    BC  Canada  49.234673 -123.155389
8                  Killarney  Vancouver    BC  Canada  49.224274 -123.046250
9                  Kitsilano  Vancouver    BC  Canada  49.269410 -123.155267
10                   Marpole  Vancouver    BC  Canada  49.209223 -123.136150
11            Mount Pleasant  Vancouver    BC  Canada  49.263330 -123.096588
12                  Oakridge  Vancouver    BC  Canada  49.230829 -123.131134
13       Renfrew-Collingwood  Vancouver    BC  Canada  49.242024 -123.057679
14                Riley Park  Vancouver    BC  Canada  49.247438 -123.102966
15               Shaughnessy  Vancouver    BC  Canada  49.251863 -123.138023
16              South Cambie  Vancouver    BC  Canada  49.246685 -123.120915
17                Strathcona  Vancouver    BC  Canada  49.279554 -123.089979
18                    Sunset  Vancouver    BC  Canada  49.219593 -123.090239
19       Victoria-Fraserview  Vancouver    BC  Canada  49.218416 -123.073287
20                  West End  Vancouver    BC  Canada  49.284131 -123.131795
21           West Point Grey  Vancouver    BC  Canada  49.264484 -123.185433

In [ ]:
# add clustering labels
vnc_merged['Cluster Labels'] = kmeans_vnc.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
vnc_merged = vnc_merged.join(vnc_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

vnc_merged.head() # check the last columns!

Neighbourhood  ... 20th Most Common Venue
0       Arbutus Ridge  ...               Bus Stop
1            Downtown  ...         Cosmetics Shop
2   Dunbar-Southlands  ...         Ice Cream Shop
3            Fairview  ...       Toy / Game Store
4  Grandview-Woodland  ...       Tapas Restaurant

[5 rows x 27 columns]

In [ ]:
vnc_merged.shape

(22, 27)

In [ ]:
df_city.loc[df_city['City']=='Vancouver', 'Longitude']

3   -123.113953
Name: Longitude, dtype: float64

In [ ]:
vnc_lng = df_city.loc[df_city['City']=='Vancouver', 'Longitude'][3]
vnc_lat = df_city.loc[df_city['City']=='Vancouver', 'Latitude'][3]

In [ ]:
map_city_clusters(vnc_merged, vnc_lng, vnc_lat)

In [ ]:
vnc_merged.groupby('Cluster Labels').count()

Neighbourhood  ...  20th Most Common Venue
Cluster Labels                 ...                        
0                           1  ...                       1
1                          11  ...                      11
2                           1  ...                       1
3                           2  ...                       2
4                           3  ...                       3
5                           2  ...                       2
6                           1  ...                       1
7                           1  ...                       1

[8 rows x 26 columns]

## Vancouver Clusters

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==0,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
17    Strathcona               0  ...              Nightclub            Cheese Shop

[1 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==1,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
0      Arbutus Ridge  ...                Bus Stop
2  Dunbar-Southlands  ...          Ice Cream Shop
5   Hastings-Sunrise  ...                   Diner
7         Kerrisdale  ...             Pizza Place
8          Killarney  ...          Cosmetics Shop

[5 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==2,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
21  West Point Grey  ...                Gym Pool

[1 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==3,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
1       Downtown  ...          Cosmetics Shop
20      West End  ...                   Beach

[2 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==4,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...         20th Most Common Venue
3       Fairview  ...               Toy / Game Store
9      Kitsilano  ...                          Beach
14    Riley Park  ...  Vegetarian / Vegan Restaurant

[3 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==5,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
6   Kensington-Cedar Cottage  ...                   Plaza
13       Renfrew-Collingwood  ...       Convenience Store

[2 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==6,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
4  Grandview-Woodland  ...        Tapas Restaurant

[1 rows x 22 columns]

In [ ]:
vnc_merged.loc[vnc_merged['Cluster Labels']==7,vnc_merged.columns[[0] + list(range(6, vnc_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
11  Mount Pleasant  ...       Indian Restaurant

[1 rows x 22 columns]

## San Francisco Map

In [ ]:
sfr_grouped = pd.read_excel("/content/Neighbourhoods_onehot_Venues_Categories.xlsx", sheet_name="sfrvenues")
sfr_grouped

Neighbourhood  Accessories Store  ...  Yoga Studio  Zoo Exhibit
0          Alamo Square                  1  ...            2            0
1            Anza Vista                  0  ...            2            0
2       Ashbury Heights                  0  ...            0            0
3           Balboa Park                  0  ...            0            0
4        Balboa Terrace                  0  ...            0            0
..                  ...                ...  ...          ...          ...
109       Vista del Mar                  0  ...            0            0
110         West Portal                  0  ...            1            0
111    Western Addition                  1  ...            1            0
112  Westwood Highlands                  0  ...            0            0
113       Westwood Park                  0  ...            0            0

[114 rows x 399 columns]

In [ ]:
# set number of clusters
kclusters = 8

sfr_grouped_clustering = sfr_grouped.drop('Neighbourhood', axis=1)

# run k-means clustering
kmeans_sfr = KMeans(n_clusters=kclusters, random_state=0).fit(sfr_grouped_clustering)

# check cluster labels generated for each row in the dataframe
len(kmeans_sfr.labels_)

114

In [ ]:
sfr_merged = df_neigh.loc[df_neigh['City']=='San Francisco']
sfr_merged = sfr_merged[sfr_merged['Neighbourhood'].isin(sfr_grouped['Neighbourhood'])].reset_index(drop=True)
sfr_merged

Neighbourhood           City State Country   Latitude   Longitude
0          Alamo Square  San Francisco    CA     USA  37.776360 -122.434689
1            Anza Vista  San Francisco    CA     USA  37.780836 -122.443149
2       Ashbury Heights  San Francisco    CA     USA  33.767144  -84.274288
3           Balboa Park  San Francisco    CA     USA  37.721427 -122.447547
4        Balboa Terrace  San Francisco    CA     USA  32.809471 -117.208557
..                  ...            ...   ...     ...        ...         ...
109       Vista del Mar  San Francisco    CA     USA  49.990345 -125.227733
110         West Portal  San Francisco    CA     USA  37.741141 -122.465634
111    Western Addition  San Francisco    CA     USA  37.779559 -122.429810
112  Westwood Highlands  San Francisco    CA     USA  14.286750  120.944712
113       Westwood Park  San Francisco    CA     USA  49.277466 -122.777594

[114 rows x 6 columns]

In [ ]:
# add clustering labels
sfr_merged['Cluster Labels'] = kmeans_sfr.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
sfr_merged = sfr_merged.join(sfr_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

sfr_merged.head() # check the last columns!

Neighbourhood           City  ... 19th Most Common Venue 20th Most Common Venue
0     Alamo Square  San Francisco  ...                 Bakery               Wine Bar
1       Anza Vista  San Francisco  ...        Bubble Tea Shop                 Market
2  Ashbury Heights  San Francisco  ...         Farmers Market             Food Truck
3      Balboa Park  San Francisco  ...             Poke Place                   Café
4   Balboa Terrace  San Francisco  ...  Vietnamese Restaurant    Japanese Restaurant

[5 rows x 27 columns]

In [ ]:
sfr_merged.shape

(114, 27)

In [ ]:
df_city.loc[df_city['City']=='San Francisco', 'Longitude']

1   -122.419906
Name: Longitude, dtype: float64

In [ ]:
sfr_lng = df_city.loc[df_city['City']=='San Francisco', 'Longitude'][1]
sfr_lat = df_city.loc[df_city['City']=='San Francisco', 'Latitude'][1]

In [ ]:
map_city_clusters(sfr_merged, sfr_lng, sfr_lat)

In [ ]:
sfr_merged.groupby('Cluster Labels').count()

Neighbourhood  ...  20th Most Common Venue
Cluster Labels                 ...                        
0                          19  ...                      19
1                          37  ...                      37
2                           8  ...                       8
3                          16  ...                      16
4                           1  ...                       1
5                          13  ...                      13
6                          11  ...                      11
7                           9  ...                       9

[8 rows x 26 columns]

## San Francisco Clusters

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==0,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
8         Buena Vista  ...             Sports Club
16  Clarendon Heights  ...                   Field
17        Cole Valley  ...                Wine Bar
19         Cow Hollow  ...          Clothing Store
32  Fisherman's Wharf  ...              Donut Shop

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==1,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
2             Ashbury Heights  ...              Food Truck
4              Balboa Terrace  ...     Japanese Restaurant
5                     Bayview  ...             Gas Station
9   Butchertown (Old and New)  ...          Breakfast Spot
12             Cayuga Terrace  ...              Food Stand

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==2,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...           20th Most Common Venue
13               China Basin  ...         Mediterranean Restaurant
26               Embarcadero  ...                             Pier
30        Financial District  ...                      Men's Store
31  Financial District South  ...                      Men's Store
67               Mission Bay  ...  Southern / Soul Food Restaurant

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==3,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...    20th Most Common Venue
7    Bernal Heights  ...               Yoga Studio
10           Castro  ...                       Gym
18   Corona Heights  ...              Burger Joint
23         Dogpatch  ...  Mediterranean Restaurant
24  Dolores Heights  ...                       Pub

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==4,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  Cluster Labels  ... 19th Most Common Venue 20th Most Common Venue
83    Polk Gulch               4  ...      Mobile Phone Shop     Frozen Yogurt Shop

[1 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==5,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
6     Belden Place  ...                Wine Bar
11  Cathedral Hill  ...             Curling Ice
14       Chinatown  ...            Cocktail Bar
15    Civic Center  ...                     Gym
46  Jackson Square  ...   Portuguese Restaurant

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==6,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...           20th Most Common Venue
3          Balboa Park  ...                             Café
28           Excelsior  ...                   Scenic Lookout
41           Ingleside  ...                       Poke Place
42  Ingleside Terraces  ...                   Sandwich Place
50         Lake Street  ...  Southern / Soul Food Restaurant

[5 rows x 22 columns]

In [ ]:
sfr_merged.loc[sfr_merged['Cluster Labels']==7,sfr_merged.columns[[0] + list(range(6, sfr_merged.shape[1]))]].head()

Neighbourhood  ...  20th Most Common Venue
0   Alamo Square  ...                Wine Bar
1     Anza Vista  ...                  Market
29      Fillmore  ...                    Park
38  Hayes Valley  ...         Bubble Tea Shop
47     Japantown  ...     Japanese Restaurant

[5 rows x 22 columns]

## Save output DataFrames in one Excel File

In [ ]:
#save dataframes to an excel file
with pd.ExcelWriter('Neighbourhoods_Clusters_with_Venues_Categories.xlsx') as writer:  
    blr_merged.to_excel(writer, sheet_name='blr_clusters', index=False)
    sul_merged.to_excel(writer, sheet_name='sul_clusters', index=False)
    vnc_merged.to_excel(writer, sheet_name='vnc_clusters', index=False)
    sfr_merged.to_excel(writer, sheet_name='sfr_clusters', index=False)

# **7. Complete Clustering**

In [ ]:
def onehot_comp_df(df_venues):
    df_onehot = pd.get_dummies(df_venues[['Venue Category']], prefix="", prefix_sep="")
    df_onehot['Neighbourhood'] = df_venues['Neighbourhood'] 
    df_onehot['City'] = df_venues['City']
    # move neighborhood column to the first column
    fixed_columns = [df_onehot.columns[-1]] + [df_onehot.columns[-2]] + list(df_onehot.columns[:-2])
    df_onehot = df_onehot[fixed_columns]

    return df_onehot

In [ ]:
def return_most_common_venues_comp(row, num_top_venues):
    row_categories = row.iloc[2:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [ ]:
def sorted_comp_dataframe(df_grouped):
    num_top_venues = 20

    indicators = ['st', 'nd', 'rd']

    # create columns according to number of top venues
    columns = ['Neighbourhood', 'City']
    for ind in np.arange(num_top_venues):
        try:
            columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
        except:
            columns.append('{}th Most Common Venue'.format(ind+1))

    # create a new dataframe
    df_venues_sorted = pd.DataFrame(columns=columns)
    df_venues_sorted['Neighbourhood'] = df_grouped['Neighbourhood']
    df_venues_sorted['City'] = df_grouped['City']
    for ind in np.arange(df_grouped.shape[0]):
        df_venues_sorted.iloc[ind, 2:] = return_most_common_venues_comp(df_grouped.iloc[ind, :], num_top_venues)

    return df_venues_sorted

In [ ]:
#import data
df_blrvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="blrvenues")
df_sulvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="sulvenues")
df_vncvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="vncvenues")
df_sfrvenues = pd.read_excel("/content/Neighbourhoods_with_Venues.xlsx", sheet_name="sfrvenues")

In [ ]:
df_blrvenues['City']='Bengaluru'
df_sulvenues['City']='Seoul'
df_vncvenues['City']='Vancouver'
df_sfrvenues['City']='San Francisco'

In [ ]:
df_blrvenues

Neighbourhood  ...       City
0       Kempegowda  ...  Bengaluru
1       Kempegowda  ...  Bengaluru
2       Kempegowda  ...  Bengaluru
3       Kempegowda  ...  Bengaluru
4     Chowdeshwari  ...  Bengaluru
...            ...  ...        ...
5047   Hemmigepura  ...  Bengaluru
5048   Hemmigepura  ...  Bengaluru
5049   Hemmigepura  ...  Bengaluru
5050   Hemmigepura  ...  Bengaluru
5051   Hemmigepura  ...  Bengaluru

[5052 rows x 8 columns]

In [ ]:
comp_venues = pd.concat([df_blrvenues, df_sulvenues, df_vncvenues, df_sfrvenues], ignore_index=True)
comp_venues.shape

(15859, 8)

In [ ]:
comp_venues

Neighbourhood  ...           City
0         Kempegowda  ...      Bengaluru
1         Kempegowda  ...      Bengaluru
2         Kempegowda  ...      Bengaluru
3         Kempegowda  ...      Bengaluru
4       Chowdeshwari  ...      Bengaluru
...              ...  ...            ...
15854  Westwood Park  ...  San Francisco
15855  Westwood Park  ...  San Francisco
15856  Westwood Park  ...  San Francisco
15857  Westwood Park  ...  San Francisco
15858  Westwood Park  ...  San Francisco

[15859 rows x 8 columns]

In [ ]:
comp_onehot = onehot_comp_df(comp_venues)
comp_onehot

City  Neighbourhood  ATM  ...  Yoga Studio  Zoo  Zoo Exhibit
0          Bengaluru     Kempegowda    0  ...            0    0            0
1          Bengaluru     Kempegowda    0  ...            0    0            0
2          Bengaluru     Kempegowda    0  ...            0    0            0
3          Bengaluru     Kempegowda    0  ...            0    0            0
4          Bengaluru   Chowdeshwari    0  ...            0    0            0
...              ...            ...  ...  ...          ...  ...          ...
15854  San Francisco  Westwood Park    0  ...            0    0            0
15855  San Francisco  Westwood Park    0  ...            0    0            0
15856  San Francisco  Westwood Park    0  ...            0    0            0
15857  San Francisco  Westwood Park    0  ...            0    0            0
15858  San Francisco  Westwood Park    0  ...            0    0            0

[15859 rows x 489 columns]

In [ ]:
comp_grouped=comp_onehot.groupby(['Neighbourhood','City']).sum().reset_index()
comp_grouped

Neighbourhood           City  ...  Zoo  Zoo Exhibit
0              A.Narayanapura      Bengaluru  ...    0            0
1                     Adugodi      Bengaluru  ...    0            0
2                      Agaram      Bengaluru  ...    0            0
3        Agrahara Dasarahalli      Bengaluru  ...    0            0
4                Alamo Square  San Francisco  ...    0            0
..                        ...            ...  ...  ...          ...
345            Yelachenahalli      Bengaluru  ...    0            0
346  Yelahanka Satellite Town      Bengaluru  ...    0            0
347           Yeongdeungpo-gu          Seoul  ...    0            0
348              Yeshwanthpur      Bengaluru  ...    0            0
349                Yongsan-gu          Seoul  ...    0            0

[350 rows x 489 columns]

In [ ]:
comp_venues_sorted = sorted_comp_dataframe(comp_grouped)
comp_venues_sorted

Neighbourhood  ...       20th Most Common Venue
0              A.Narayanapura  ...                         Food
1                     Adugodi  ...  Eastern European Restaurant
2                      Agaram  ...                    Irish Pub
3        Agrahara Dasarahalli  ...            Food & Drink Shop
4                Alamo Square  ...                   Restaurant
..                        ...  ...                          ...
345            Yelachenahalli  ...                       Forest
346  Yelahanka Satellite Town  ...            Food & Drink Shop
347           Yeongdeungpo-gu  ...                Shopping Mall
348              Yeshwanthpur  ...                        Diner
349                Yongsan-gu  ...            Bunsik Restaurant

[350 rows x 22 columns]

In [ ]:
# set number of clusters
kclusters = 8

comp_grouped_clustering = comp_grouped.drop(['Neighbourhood','City'], axis=1)

# run k-means clustering
kmeans_comp = KMeans(n_clusters=kclusters, random_state=0).fit(comp_grouped_clustering)

# check cluster labels generated for each row in the dataframe
len(kmeans_comp.labels_)

350

In [ ]:
comp_merged = df_neigh.copy()
comp_merged = comp_merged[comp_merged['Neighbourhood'].isin(comp_grouped['Neighbourhood'])].reset_index(drop=True)
comp_merged.shape

(350, 6)

In [ ]:
comp_merged

Neighbourhood           City  ...   Latitude   Longitude
0                  Kempegowda      Bengaluru  ...  13.109018   77.601900
1                Chowdeshwari      Bengaluru  ...  12.925190   77.588020
2                       Attur      Bengaluru  ...  13.111482   77.563056
3    Yelahanka Satellite Town      Bengaluru  ...  13.089139   77.582717
4                      Jakkur      Bengaluru  ...  13.078474   77.606894
..                        ...            ...  ...        ...         ...
345             Vista del Mar  San Francisco  ...  49.990345 -125.227733
346               West Portal  San Francisco  ...  37.741141 -122.465634
347          Western Addition  San Francisco  ...  37.779559 -122.429810
348        Westwood Highlands  San Francisco  ...  14.286750  120.944712
349             Westwood Park  San Francisco  ...  49.277466 -122.777594

[350 rows x 6 columns]

In [ ]:
# add clustering labels
comp_merged['Cluster Labels'] = kmeans_comp.labels_

comp_merged = comp_merged.join(comp_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood', lsuffix='', rsuffix='_right')

comp_merged.head()

Neighbourhood  ... 20th Most Common Venue
0                Kempegowda  ...                 Forest
1              Chowdeshwari  ...              Bookstore
2                     Attur  ...             Food Stand
3  Yelahanka Satellite Town  ...      Food & Drink Shop
4                    Jakkur  ...       Football Stadium

[5 rows x 28 columns]

In [ ]:
map_city_clusters(comp_merged, blr_lng, blr_lat)

In [ ]:
map_city_clusters(comp_merged, sul_lng, sul_lat)

In [ ]:
map_city_clusters(comp_merged, vnc_lng, vnc_lat)

In [ ]:
map_city_clusters(comp_merged, sfr_lng, sfr_lat)

In [ ]:
comp_merged.groupby(['Cluster Labels','City']).count()

Neighbourhood  ...  20th Most Common Venue
Cluster Labels City                          ...                        
0              Bengaluru                 87  ...                      87
               San Francisco             48  ...                      48
               Seoul                      8  ...                       8
               Vancouver                 14  ...                      14
1              Bengaluru                 12  ...                      12
               San Francisco              6  ...                       6
               Seoul                      1  ...                       1
2              Bengaluru                 35  ...                      35
               San Francisco             18  ...                      18
               Seoul                      8  ...                       8
3              Bengaluru                  4  ...                       4
               San Francisco              6  ...                       6
4              Bengaluru                  3  ...                       3
               San Francisco              6  ...                       6
5              Bengaluru                 22  ...                      22
               San Francisco             11  ...                      11
               Seoul                      4  ...                       4
               Vancouver                  5  ...                       5
6              Bengaluru                 10  ...                      10
               San Francisco              6  ...                       6
               Seoul                      2  ...                       2
               Vancouver                  2  ...                       2
7              Bengaluru                 16  ...                      16
               San Francisco             13  ...                      13
               Seoul                      2  ...                       2
               Vancouver                  1  ...                       1

[26 rows x 26 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==0,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
5        Thanisandra  ...        Football Stadium
7        Kodigehalli  ...                  Forest
9   Doddabommasandra  ...                  Island
10     Kuvempu Nagar  ...                  Forest
11       Mallasandra  ...       Food & Drink Shop

[5 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==1,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
8                     Vidyaranyapura  ...             Gaming Cafe
20             Vishwanathnagenahalli  ...             Flea Market
46                    Lingarajapuram  ...      Dim Sum Restaurant
68                      Kottigepalya  ...             Flea Market
72                Dattathreya Temple  ...      Italian Restaurant
105                Sampangiram Nagar  ...          Sandwich Place
112                    Shanthi Nagar  ...                     Pub
129              Jagareevanram Nagar  ...                  Forest
149  Gali Anjaneya Swamy Temple Ward  ...           Garden Center
150                 Deepanjali Nagar  ...             Fish Market
151                          Kengeri  ...              Food Stand
178                      Bilekahalli  ...           Garden Center
208                      Seongbuk-gu  ...         Bed & Breakfast
246                           Castro  ...                Wine Bar
255                       Cow Hollow  ...             Yoga Studio
275                    Hunters Point  ...     Filipino Restaurant
282                   Jackson Square  ...           Grocery Store
300                  Midtown Terrace  ...              Food Court
336                  Sunset District  ...           Grocery Store

[19 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==2,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
0                  Kempegowda  ...                  Forest
1                Chowdeshwari  ...               Bookstore
2                       Attur  ...              Food Stand
3    Yelahanka Satellite Town  ...       Food & Drink Shop
13              T-Dasarahalli  ...             Zoo Exhibit
..                        ...  ...                     ...
303               Mission Bay  ...                     Spa
304          Mission District  ...          Clothing Store
306           Mission Terrace  ...                    Farm
308            Mount Davidson  ...             Bus Station
335                 Sunnydale  ...    Cantonese Restaurant

[61 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==3,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
69   Shakthiganapathi Nagar  ...       Fish & Chips Shop
94             Rajaji Nagar  ...              Food Stand
106         Shanthala Nagar  ...              Steakhouse
154              Giri Nagar  ...       French Restaurant
278      Ingleside Terraces  ...             Supermarket
279            Inner Sunset  ...              Taco Place
280              Irish Hill  ...      Basketball Stadium
281            Islais Creek  ...           Shopping Mall
347        Western Addition  ...              Playground
349           Westwood Park  ...             Flea Market

[10 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==4,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
26         Kammanahalli  ...           Fishing Store
88        Vasanth Nagar  ...             Planetarium
123  Jnanabharathi Ward  ...                Fountain
273      Haight-Ashbury  ...       Accessories Store
285        Laguna Honda  ...     Japanese Restaurant
289      Laurel Heights  ...              Bagel Shop
299      Merced Heights  ...      Light Rail Station
319          Polk Gulch  ...      Mexican Restaurant
324    Presidio Heights  ...               Pet Store

[9 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==5,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
4                         Jakkur  ...        Football Stadium
6                Byatarayanapura  ...                    Food
28              Kadugondanahalli  ...              Food Stand
33                 Aramane Nagar  ...          Sandwich Place
37              Dodda Bidarkallu  ...                  Forest
49                     K.R.Puram  ...              Food Truck
50                  Basavanapura  ...        Football Stadium
52                    Devasandra  ...   Rajasthani Restaurant
57                   Sagayapuram  ...       Electronics Store
66                  Hegganahalli  ...                Fountain
67                     Herohalli  ...                Fountain
78                      Kadugudi  ...              Food Stand
81                    Marathalli  ...             Fish Market
84                     Jogupalya  ...      Mexican Restaurant
85                        Ulsoor  ...              Steakhouse
100         Agrahara Dasarahalli  ...       Food & Drink Shop
114  Dharmarayaswamy Temple Ward  ...           Fishing Store
118                  Vijay Nagar  ...                Fountain
135                 Sunkenahalli  ...           Garden Center
136              Visvesvarapuram  ...   General Entertainment
145                     Jayangar  ...                  Bakery
155                   Katriguppe  ...       Food & Drink Shop
195                   Gangnam-gu  ...       Indian Restaurant
196                   Gangseo-gu  ...              Food Stand
198                      Guro-gu  ...              Steakhouse
209                 Seongdong-gu  ...         Soba Restaurant
219             Hastings-Sunrise  ...            Burger Joint
231                   Strathcona  ...                     Gym
232                       Sunset  ...             Coffee Shop
233          Victoria-Fraserview  ...        Sushi Restaurant
234                     West End  ...     American Restaurant
239                  Balboa Park  ...     Fried Chicken Joint
241                      Bayview  ...             Golf Course
245    Butchertown (Old and New)  ...               Rock Club
250                    Chinatown  ...          Cosmetics Shop
251                 Civic Center  ...            Dance Studio
254               Corona Heights  ...                  Museum
269                  Forest Hill  ...                     Bar
272          Golden Gate Heights  ...    Fast Food Restaurant
311                  North Beach  ...            Gourmet Shop
339              Treasure Island  ...              Food Stand
340                   Twin Peaks  ...      Italian Restaurant

[42 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==6,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...  20th Most Common Venue
25            Banaswadi  ...       Fish & Chips Shop
44   Devarajeevanahalli  ...       French Restaurant
45     Muneshwara Nagar  ...       French Restaurant
47       Benniganahalli  ...              Donut Shop
73      Pulikeshi Nagar  ...          Sandwich Place
76        Vignana Nagar  ...                Fountain
82          HAL Airport  ...             Zoo Exhibit
83    Jeevanbhima Nagar  ...           Grocery Store
104           Chickpete  ...             Flea Market
174         Uttarahalli  ...             Gaming Cafe
194         Gangdong-gu  ...              Food Truck
197        Geumcheon-gu  ...                  Garden
218  Grandview-Woodland  ...           Grocery Store
225      Mount Pleasant  ...       Indian Restaurant
268   Fisherman's Wharf  ...                    Café
294       Lone Mountain  ...             College Gym
297      Lower Nob Hill  ...                    Café
298     Marina District  ...             Salad Place
312  North of Panhandle  ...             Yoga Studio
318           Parnassus  ...             Yoga Studio

[20 rows x 23 columns]

In [ ]:
comp_merged.loc[comp_merged['Cluster Labels']==7,comp_merged.columns[[0] + list(range(6, comp_merged.shape[1]))]]

Neighbourhood  ...      20th Most Common Venue
15                   J.P.Park  ...                 Pizza Place
38     Peenya Industrial Area  ...           Fish & Chips Shop
70               Shankaramata  ...           Food & Drink Shop
71             Gayathri Nagar  ...  Financial or Legal Service
77            Garudacharpalya  ...               Movie Theater
79                  Hagadooru  ...           Food & Drink Shop
80              Doddanekkundi  ...                        Fair
107                    Domlur  ...        Fast Food Restaurant
109                    Agaram  ...                   Irish Pub
117        Kempapura Agrahara  ...               Fishing Store
133                Chamrajpet  ...                Intersection
134                Azad Nagar  ...                      Garden
140                   Ejipura  ...       General Entertainment
171        Kumaraswamy Layout  ...                  Food Stand
172          Padmanabha Nagar  ...         Filipino Restaurant
185               Konanakunte  ...                        Farm
192              Eunpyeong-gu  ...           Food & Drink Shop
210                 Songpa-gu  ...                  Food Truck
217                  Fairview  ...         American Restaurant
240            Balboa Terrace  ...          Chinese Restaurant
249               China Basin  ...            Basketball Court
265                  Fillmore  ...                         Spa
266        Financial District  ...                        Park
267  Financial District South  ...                        Park
291          Little Hollywood  ...                   Juice Bar
295              Lower Haight  ...                   BBQ Joint
301                Mid-Market  ...            Football Stadium
309                  Nob Hill  ...                   Pet Store
317                Parkmerced  ...            Sushi Restaurant
320                   Portola  ...                Soccer Field
337            Telegraph Hill  ...         Szechuan Restaurant
338                Tenderloin  ...                       Plaza

[32 rows x 23 columns]